
# Introduction

[Scrapy](https://scrapy.org/) est un framework permettant de crawler des
sites web et d'en extraire les données de façon structurée.

## Installation

Nous travaillerons dans un environnement
[Anaconda](https://www.anaconda.com/download/), déjà présent sur les
machines de l'ESIEE. Sur vos machines personnelles, télécharger la
distribution correspondant à la version la plus récente de Python.

[Scrapy](https://scrapy.org/) ne fait pas partie de la distribution par
défaut de Python et doit être installé manuellement. Ici, le package est
déjà installé grâce à Pipenv.

Si vous avez besoin d'installer dans un autre cadre.

-   Avec **Pipenv** : `pipenv install scrapy`
-   Avec **Anaconda** : `conda install -c conda-forge scrapy`

Tester la réussite de l'opération dans un interpréteur Python. Avant
installation:

In [2]:
!pip install scrapy

In [3]:
import scrapy

## Architecture

[Scrapy](https://scrapy.org/) est un framework comportant plusieurs
composants.

<img src="images/architecture.png" alt="image" class="align-center" />

L'ensemble du processus est contrôlé par l'**engine** (les termes anglo
saxons ont été retenus pour un meilleur référencement dans la
[documentation officielle](https://docs.scrapy.org/en/latest/)).

Le framework est articulé avec plusieurs composants qui gèrent chacun un
rôle différent. Nous allons les détailler.

-   Les **Spiders** : permettent de naviguer sur un site et de
    référencer les règles d'extraction de la donnée.
-   Les **Pipelines** : font le lien entre la donnée brute et des objets
    structurés
-   Les **Middlewares** : permettent d'effectuer des transformations sur
    les objets ou sur les requêtes exécutées par l'engine.
-   Le **Scheduler** : gère l'ordre et le timing des requêtes
    effectuées.

## Fonctionnement

[Scrapy](https://scrapy.org/) est entièrement organisé autour d'un
composant central : l'*engine*.

Le rôle de l'*engine* est de contrôler le flux de données entre les
différents composants du système.

1.  En particulier, il est chargé de récupérer les *requests* définies
    dans les *spiders*
2.  Ces *requests* sont ensuite fournies au *scheduler* qui se charge de
    leur ordonnancement
3.  Les *requests* sont présentées selon cet ordonnancement à
    l'*engine*...
4.  ... qui les transmet au *downloader*
5.  Le *downloader* effectue la *request* et transmet la *response* (le
    contenu de la page web) à l'*engine*...
6.  ... puis l'envoie au *spider* pour traitement
7.  Le *spider* génére des *items* qui sont transmis à l'*engine*
8.  Les *items* sont ensuite poussés dans un pipeline pour nettoyage,
    validation et stockage

Ce processus est répété jusqu'à épuisement des requêtes.

[Scrapy](https://scrapy.org/) est un [framework orienté
événements](https://en.wikipedia.org/wiki/Event-driven_architecture)
(basé sur [Twisted](https://twistedmatrix.com/)) permettant une
programmation asynchrone (non bloquante). C'est particulièrement
intéressant dans les opérations de scraping, puisque **le programme
n'attend pas le résultat d'une requête pour en lancer une autre**.

En effet, lorsque l'on sollicite une ressource (requête réseau, système
de fichier, etc.) en mode bloquant, l'exécution du programme est
suspendue le temps que la transaction avec la ressource se termine (par
exemple le temps qu'une page web soit complètement téléchargée).
L'intérêt de faire des appels non bloquants, c'est que l'on peut gérer
de multiples téléchargements en parallèle, et que le programme peut
continuer à tourner pendant ce temps.

# Un scraping élémentaire

Avant de rentrer dans les détails du framework, nous allons mettre en
oeuvre un premier script permettant de récupérer l'information présente
sur [la page web](http://evene.lefigaro.fr/citations/winston-churchill)
recensant les citations de [Sir Winston
Churchill](https://en.wikipedia.org/wiki/Winston_Churchill).

**Exercice**

Examiner le code source de cette page avec l'inspecteur de votre
navigateur. Identifier les éléments contenant l'information recherchée,
ici la chaîne de caractères contenant la citation proprement dite.

## Le code source

Le code utilisé est le suivant:

In [4]:
# %load citations_churchill_spider1.py
import scrapy

class ChurchillQuotesSpider(scrapy.Spider):
    name = "citations de Churchill"
    start_urls = ["http://evene.lefigaro.fr/citations/winston-churchill",]

    def parse(self, response):
        for cit in response.xpath('//div[@class="figsco__quote__text"]'):
            text_value = cit.xpath('a/text()').extract_first()
            yield { 'text' : text_value }

## Le fonctionnement

Le fonctionnement est le suivant:

-   On importe le module [Scrapy](https://scrapy.org/) (3)
-   et on définit une sous classe de `scrapy.Spider` (5)
-   la variable `start_urls` contient la liste des pages à scraper (7)
-   On redéfinit la méthode $parse$ dont la signature est définie dans
    la classe mère (9)
-   L'objet
    [response](https://docs.scrapy.org/en/latest/topics/request-response.html#response-objects)
    représente la réponse à la requête HTTP (l'attribut $text$ permet
    d'accéder à son contenu). On recherche ensuite tous les containers
    `<div>` identifiés dans l'exercice précédent. Ici la page est
    particulièrement bien structurée et les citations disposent de leur
    propre container, identifié par l'attribut `class` de valeur
    `figsco__quote__text`. La sélection se fait par une expression
    [XPath](https://en.wikipedia.org/wiki/XPath), un langage de
    sélection de noeud dans un document XML (10). En langage naturel, la
    requête pourrait se formuler : "On recherche tous les containers
    `<div>` dont la valeur de l'attribut `class` est égal à
    `figsco__quote__text`".
-   Pour chaque résultat, on construit un dictionnaire dont la clé est
    `text` et la valeur le contenu du lien `<a>`. Ce résultat est fourni
    par un générateur ($yield$) (12).

On lance le scraping depuis un terminal:

In [5]:
!scrapy runspider citations_churchill_spider1.py

2021-11-30 12:21:52 [scrapy.utils.log] INFO: Scrapy 2.4.0 started (bot: scrapybot)
2021-11-30 12:21:52 [scrapy.utils.log] INFO: Versions: lxml 4.6.4.0, libxml2 2.9.10, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 20.3.0, Python 3.8.12 (default, Nov 17 2021, 16:58:51) - [GCC 10.2.1 20210110], pyOpenSSL 19.1.0 (OpenSSL 1.1.1h  22 Sep 2020), cryptography 3.2.1, Platform Linux-5.10.16.3-microsoft-standard-WSL2-x86_64-with-glibc2.2.5
2021-11-30 12:21:52 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.epollreactor.EPollReactor
2021-11-30 12:21:52 [scrapy.crawler] INFO: Overridden settings:
{'SPIDER_LOADER_WARN_ONLY': True}
2021-11-30 12:21:52 [scrapy.extensions.telnet] INFO: Telnet Password: 9b042bcd4ea6dc9b
2021-11-30 12:21:52 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.extensions.memusage.MemoryUsage',
 'scrapy.extensions.logstats.LogStats']
2021-11-30 12:21:52 [scrapy.middlewa

On y trouve des informations sur les paramètres
utilisés:

In [ ]:
2018-01-10 17:21:05 [scrapy.utils.log] INFO: Scrapy 1.4.0 started (bot: scrapybot)
2018-01-10 17:21:05 [scrapy.utils.log] INFO: Overridden settings: {'SPIDER_LOADER_WARN_ONLY': True}

les
[extensions](https://docs.scrapy.org/en/latest/topics/extensions.html)
...:

In [ ]:
2018-01-10 17:21:05 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
'scrapy.extensions.telnet.TelnetConsole',
'scrapy.extensions.logstats.LogStats']

[Les composants middleware
downloader](https://docs.scrapy.org/en/latest/topics/downloader-middleware.html)
... :

In [ ]:
2018-01-10 17:21:05 [scrapy.middleware] INFO: Enabled downloader middlewares:
['scrapy.downloadermiddlewares.httpauth.HttpAuthMiddleware',
'scrapy.downloadermiddlewares.downloadtimeout.DownloadTimeoutMiddleware',
'scrapy.downloadermiddlewares.defaultheaders.DefaultHeadersMiddleware',
'scrapy.downloadermiddlewares.useragent.UserAgentMiddleware',
'scrapy.downloadermiddlewares.retry.RetryMiddleware',
'scrapy.downloadermiddlewares.redirect.MetaRefreshMiddleware',
'scrapy.downloadermiddlewares.httpcompression.HttpCompressionMiddleware',
'scrapy.downloadermiddlewares.redirect.RedirectMiddleware',
'scrapy.downloadermiddlewares.cookies.CookiesMiddleware',
'scrapy.downloadermiddlewares.httpproxy.HttpProxyMiddleware',
'scrapy.downloadermiddlewares.stats.DownloaderStats']

Idem pour [les composants middleware
spider](https://docs.scrapy.org/en/latest/topics/spider-middleware.html)
...:

In [ ]:
2018-01-10 17:21:05 [scrapy.middleware] INFO: Enabled spider middlewares:
['scrapy.spidermiddlewares.httperror.HttpErrorMiddleware',
'scrapy.spidermiddlewares.offsite.OffsiteMiddleware',
'scrapy.spidermiddlewares.referer.RefererMiddleware',
'scrapy.spidermiddlewares.urllength.UrlLengthMiddleware',
'scrapy.spidermiddlewares.depth.DepthMiddleware']

Aucun
[pipeline](https://docs.scrapy.org/en/latest/topics/item-pipeline.html)
n'est activé :

In [ ]:
2018-01-10 17:21:05 [scrapy.middleware] INFO: Enabled item pipelines:
[]

**Exercice**

Identifier la position des [composants middleware
downloader](https://docs.scrapy.org/en/latest/topics/downloader-middleware.html),
des [composants middleware
spider](https://docs.scrapy.org/en/latest/topics/spider-middleware.html)
et du
[pipeline](https://docs.scrapy.org/en/latest/topics/item-pipeline.html)
dans $l'architecture <Introduction>$

L'exécution du scraping proprement dit débute :

In [ ]:
2018-01-10 17:21:05 [scrapy.core.engine] INFO: Spider opened
2018-01-10 17:21:05 [scrapy.extensions.logstats] INFO: Crawled 0 pages (at 0 pages/min), scraped 0 items (at 0 items/min)
2018-01-10 17:21:05 [scrapy.extensions.telnet] DEBUG: Telnet console listening on 127.0.0.1:6023

La première URL est poussée par le scheduler:

In [ ]:
2018-01-10 17:21:05 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://evene.lefigaro.fr/citations/winston-churchill> (referer: None)

## Les résultats

Les résultats sont fournis par le générateur défini dans la méthode
$parse$ dans un dictionnaire. Ils contiennent le texte des citations
dans la valeur de la clé `text` :

In [ ]:
2018-01-10 17:21:05 [scrapy.core.scraper] DEBUG: Scraped from <200 http://evene.lefigaro.fr/citations/winston-churchill>
{'text': '“Le vice inhérent au capitalisme consiste en une répartition inégale des richesses. La vertu inhérente au socialisme consiste en une égale répartition de la misère.”'}
2018-01-10 17:21:05 [scrapy.core.scraper] DEBUG: Scraped from <200 http://evene.lefigaro.fr/citations/winston-churchill>
{'text': "Faire le bien, éviter le mal, c'est ça le paradis."}

## Les statistiques

Une fois le scraping effectué, quelques statistiques sont affichées sur
le terminal:

In [ ]:
2018-01-10 17:21:05 [scrapy.core.engine] INFO: Closing spider (finished)
2018-01-10 17:21:05 [scrapy.statscollectors] INFO: Dumping Scrapy stats:
{'downloader/request_bytes': 242,
'downloader/request_count': 1,
'downloader/request_method_count/GET': 1,
'downloader/response_bytes': 17435,
'downloader/response_count': 1,
'downloader/response_status_count/200': 1,
'finish_reason': 'finished',
'finish_time': datetime.datetime(2018, 1, 10, 16, 21, 5, 858347),
'item_scraped_count': 16,
'log_count/DEBUG': 18,
'log_count/INFO': 7,
'response_received_count': 1,
'scheduler/dequeued': 1,
'scheduler/dequeued/memory': 1,
'scheduler/enqueued': 1,
'scheduler/enqueued/memory': 1,
'start_time': datetime.datetime(2018, 1, 10, 16, 21, 5, 645347)}
2018-01-10 17:21:05 [scrapy.core.engine] INFO: Spider closed (finished)

On observe notamment que notre code permet de récupérer la taille de la
page web (17435 bytes), le temps d'exécution à partir des valeurs
`finish_time` et `start_time`, le nombre d'items scrapés (16), etc...

**Exercice**

Les citations extraites sont elles toutes de [Sir Winston
Churchill](https://en.wikipedia.org/wiki/Winston_Churchill) ? Il sera
peut être nécessaire de modifier le sélecteur XPath. Nous verrons ça
lorsque il faudra récupérer les données relative à l'auteur.

## Modifier les données

Il est parfois nécessaire de faire un traitement sur les données
scrapées, pour ajouter ou retirer de l'information.

**Exercice**

Retirer les caractères `“` et `”` qui délimitent la citation. Ces
caractères sont identifiés en Unicode comme [LEFT DOUBLE QUOTATION
MARK](http://www.fileformat.info/info/unicode/char/201c/index.htm) et
[RIGHT DOUBLE QUOTATION
MARK](http://www.fileformat.info/info/unicode/char/201d/index.htm).

## Plus de données

Il est souvent nécessaire de récupérer plusieurs informations relatives
à un même item. Dans cet exemple, il est judicieux d'associer à la
citation le nom de son auteur, en allant chercher cette information au
plus près du texte lui même.

**Exercice**

Examiner le code source de la page web et identifier la structuration de
la donnée associée à l'auteur. En déduire l'expression XPath permettant
de la récupérer. S'assurer que seules les citations de [Sir Winston
Churchill](https://en.wikipedia.org/wiki/Winston_Churchill) sont
extraites. Ajouter une clé `author` au dictionnaire retourné par le
$yield$ dont la valeur est précisément la chaîne de caractères contenant
l'auteur.

Un exemple de dictionnaire retourné:

In [ ]:
{   'text': "“Si deux hommes ont toujours la même opinion, l'un d'eux est de trop.”", 
    'author': 'Winston Churchill'}

Pour lancer l'exécution de la spider :

> \$ scrapy runspider spiders/citations\_churchill\_spider2.py

On peut aussi vouloir stocker les données extraites :

> \$ scrapy runspider spiders/citations\_churchill\_spider2.py -o
> data/citation.json -t json

In [6]:
!scrapy runspider citations_churchill_spider2.py -o data/citation2.json -t json

/root/.local/share/virtualenvs/code-AFz48Hjb/lib/python3.8/site-packages/scrapy/commands/__init__.py:131: ScrapyDeprecationWarning: ('The -t command line option is deprecated in favor of specifying the output format within the output URI. See the documentation of the -o and -O options for more information.',)
  feeds = feed_process_params_from_cli(
2021-11-30 12:22:01 [scrapy.utils.log] INFO: Scrapy 2.4.0 started (bot: scrapybot)
2021-11-30 12:22:01 [scrapy.utils.log] INFO: Versions: lxml 4.6.4.0, libxml2 2.9.10, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 20.3.0, Python 3.8.12 (default, Nov 17 2021, 16:58:51) - [GCC 10.2.1 20210110], pyOpenSSL 19.1.0 (OpenSSL 1.1.1h  22 Sep 2020), cryptography 3.2.1, Platform Linux-5.10.16.3-microsoft-standard-WSL2-x86_64-with-glibc2.2.5
2021-11-30 12:22:01 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.epollreactor.EPollReactor
2021-11-30 12:22:01 [scrapy.crawler] INFO: Overridden settings:
{'SPIDER_LOADER_WARN_ONLY': True}
2021-1


# Votre premier projet


Dans un premier temps vous devez créer un projet Scrapy avec la commande
:

In [7]:
!scrapy startproject newscrawler

Error: scrapy.cfg already exists in /home/dev/code/2Scrapy/newscrawler


Cette commande va créer un dossier `monprojet` contenant les éléments
suivants correspondant au squelette :

In [ ]:
newscrawler/
    scrapy.cfg            # Options de déploiement

    newscrawler/             # Le module Python contenant les informations
        __init__.py

        items.py          # Fichier contenant les items

        middlewares.py    # Fichier contenant les middlewares

        pipelines.py      # Fichier contenant les pipelines

        settings.py       # Fichier contenant les paramètres du projet

        spiders/          # Dossier contenant toutes les spiders
            __init__.py

# Votre première Spider

Une Spider est une classe Scrapy qui permet de mettre en place toute
l'architecture complexe vue dans l'introduction. Pour définir une
spider, il vous faut hériter de la classe $scrapy.Spider$. La seule
chose à faire est de définir la première requête à effectuer et comment
suivre les liens. La Spider s'arrêtera lorsqu'elle aura parcouru tous
les liens qu'on lui a demandé de suivre.

Pour créer une Spider on utilise la syntaxe:

In [ ]:
!scrapy genspider <SPIDER_NAME> <DOMAIN_NAME>

Par exemple,

In [8]:
!cd newscrawler && scrapy genspider lemonde lemonde.fr

Spider 'lemonde' already exists in module:
  newscrawler.spiders.lemonde


Cette commande permet de créer une spider appelée `lemonde` pour scraper
le domaine `lemonde.fr`. Cela crée le fichier Python
`spiders/lemonde.py` suivant :

In [ ]:
# %load newscrawler/newscrawler/spiders/lemonde.py
import scrapy


class LemondeSpider(scrapy.Spider):
    name = 'lemonde'
    allowed_domains = ['lemonde.fr']
    start_urls = ['http://lemonde.fr/']

    def parse(self, response):
        pass


Une bonne pratique pour commencer à développer une Spider est de passer
par l'interface Shell proposée par Scrapy. Elle permet de récupérer un
objet `Response` et de tester les méthodes de récupération des données.

# ATTENTION : Les commandes scrapy shell doivent être lancées dans un terminal 

In [9]:
!scrapy shell 'http://lemonde.fr'

2021-11-30 12:23:35 [scrapy.utils.log] INFO: Scrapy 2.4.0 started (bot: scrapybot)
2021-11-30 12:23:35 [scrapy.utils.log] INFO: Versions: lxml 4.6.4.0, libxml2 2.9.10, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 20.3.0, Python 3.8.12 (default, Nov 17 2021, 16:58:51) - [GCC 10.2.1 20210110], pyOpenSSL 19.1.0 (OpenSSL 1.1.1h  22 Sep 2020), cryptography 3.2.1, Platform Linux-5.10.16.3-microsoft-standard-WSL2-x86_64-with-glibc2.2.5
2021-11-30 12:23:35 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.epollreactor.EPollReactor
2021-11-30 12:23:35 [scrapy.crawler] INFO: Overridden settings:
{'DUPEFILTER_CLASS': 'scrapy.dupefilters.BaseDupeFilter',
 'LOGSTATS_INTERVAL': 0}
2021-11-30 12:23:35 [scrapy.extensions.telnet] INFO: Telnet Password: ef3f8d7431b2b59a
2021-11-30 12:23:35 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.extensions.memusage.MemoryUsage']
2021-11-30 12:23:35 [scrapy

Accès au container, pipenv shell, pip freeze 

!scrapy shell 'http://lemonde.fr'

Pour les utilisateurs de windows il vous faut mettre des doubles quotes
:

In [ ]:
scrapy shell "http://lemonde.fr"

Scrapy lance un kernel Python

In [ ]:
2018-12-02 16:05:50 [scrapy.utils.log] INFO: Scrapy 1.3.3 started (bot: newscrawler)
2018-12-02 16:05:50 [scrapy.utils.log] INFO: Overridden settings: {'BOT_NAME': 'newscrawler', 'DUPEFILTER_CLASS': 'scrapy.dupefilters.BaseDupeFilter', 'LOGSTATS_INTERVAL': 0, 'NEWSPIDER_MODULE': 'newscrawler.spiders', 'ROBOTSTXT_OBEY': True, 'SPIDER_MODULES': ['newscrawler.spiders']}
2018-12-02 16:05:50 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
'scrapy.extensions.telnet.TelnetConsole']
2018-12-02 16:05:50 [scrapy.middleware] INFO: Enabled downloader middlewares:
['scrapy.downloadermiddlewares.robotstxt.RobotsTxtMiddleware',
'scrapy.downloadermiddlewares.httpauth.HttpAuthMiddleware',
'scrapy.downloadermiddlewares.downloadtimeout.DownloadTimeoutMiddleware',
'scrapy.downloadermiddlewares.defaultheaders.DefaultHeadersMiddleware',
'scrapy.downloadermiddlewares.useragent.UserAgentMiddleware',
'scrapy.downloadermiddlewares.retry.RetryMiddleware',
'scrapy.downloadermiddlewares.redirect.MetaRefreshMiddleware',
'scrapy.downloadermiddlewares.httpcompression.HttpCompressionMiddleware',
'scrapy.downloadermiddlewares.redirect.RedirectMiddleware',
'scrapy.downloadermiddlewares.cookies.CookiesMiddleware',
'scrapy.downloadermiddlewares.stats.DownloaderStats']
2018-12-02 16:05:50 [scrapy.middleware] INFO: Enabled spider middlewares:
['scrapy.spidermiddlewares.httperror.HttpErrorMiddleware',
'scrapy.spidermiddlewares.offsite.OffsiteMiddleware',
'scrapy.spidermiddlewares.referer.RefererMiddleware',
'scrapy.spidermiddlewares.urllength.UrlLengthMiddleware',
'scrapy.spidermiddlewares.depth.DepthMiddleware']
2018-12-02 16:05:50 [scrapy.middleware] INFO: Enabled item pipelines:
[]
2018-12-02 16:05:50 [scrapy.extensions.telnet] DEBUG: Telnet console listening on 127.0.0.1:6023
2018-12-02 16:05:50 [scrapy.core.engine] INFO: Spider opened
2018-12-02 16:05:50 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/robots.txt> (referer: None)
2018-12-02 16:05:50 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/> (referer: None)
2018-12-02 16:05:54 [traitlets] DEBUG: Using default logger
2018-12-02 16:05:54 [traitlets] DEBUG: Using default logger
[s] Available Scrapy objects:
[s]   scrapy     scrapy module (contains scrapy.Request, scrapy.Selector, etc)
[s]   crawler    <scrapy.crawler.Crawler object at 0x10fc38c18>
[s]   item       {}
[s]   request    <GET https://www.lemonde.fr/>
[s]   response   <200 https://www.lemonde.fr/>
[s]   settings   <scrapy.settings.Settings object at 0x113bb0898>
[s]   spider     <DefaultSpider 'default' at 0x113e60cc0>
[s] Useful shortcuts:
[s]   fetch(url[, redirect=True]) Fetch URL and update local objects (by default, redirects are followed)
[s]   fetch(req)                  Fetch a scrapy.Request and update local objects
[s]   shelp()           Shell help (print this help)
[s]   view(response)    View response in a browser

Grâce à cette interface, vous avez accès à plusieurs objets comme la
`Response`, la `Request`, la `Spider` par exemple. Vous pouvez aussi
exécuter `view(response)` pour afficher ce que Scrapy récupère dans un
navigateur.

In [ ]:
In [1]: response
Out[1]: <200 https://www.lemonde.fr/>

In [3]: request
Out[3]: <GET https://www.lemonde.fr/>

In [4]: type(request)
Out[4]: scrapy.http.request.Request

In [5]: spider
Out[5]: <LemondeSpider 'lemonde' at 0x1080fccc0>

In [6]: type(spider)
Out[6]: monprojet.spiders.lemonde.LeMondeSpider

Ici on voit que la Spider est une instance de LemondeSpider. Lorsqu'on
lance le $scrapy shell$ scrapy va chercher dans les spiders si une
correspond au lien passé en paramètre, si oui , il l'utilise sinon une
$DefaultSpider$ est instanciée.

## Vos premières requêtes

On peut commencer à regarder comment extraire les données de la page web
en utilisant le langage de requêtes proposé par Scrapy. Il existe deux
types de requêtes : les requêtes `css` et `xpath`. Les requêtes `xpath`
sont plus complexes mais plus puissantes que les requêtes `css`. Dans le
cadre de ce tutorial, nous allons uniquement aborder les requêtes `css`,
elles nous suffiront pour extraire les données dont nous avons besoin
(en interne, Scrapy transforme les requêtes `css`en requêtes `xpath`.

Que ce soit les requêtes `css` ou `xpath`, elles crééent des sélecteurs
de différents types. Quelques exemples :

Pour récupérer le titre d'une page :

In [ ]:
In [1]: response.css('title')
Out[1]: [<Selector xpath='descendant-or-self::title' data='<title>Le Monde.fr - Actualités et Infos'>]

On récupère une liste de sélecteurs correspondant à la requête `css`
appelée. La requête précédente était unique, d'autres requêtes moins
restrictives permettent de récupérer plusieurs résultats. Par exemple
pour rechercher l'ensemble des liens présents sur la page, on va
rechercher les balises HTML `<a></a>`

In [ ]:
In [5]: response.css("a")[0:10]
Out[5]:
[<Selector xpath='descendant-or-self::a' data='<a target="_blank" data-target="jelec-he'>,
<Selector xpath='descendant-or-self::a' data='<a href="/"> <div class="logo__lemonde l'>,
<Selector xpath='descendant-or-self::a' data='<a href="https://secure.lemonde.fr/sfuse'>,
<Selector xpath='descendant-or-self::a' data='<a href="https://abo.lemonde.fr/#xtor=CS'>,
<Selector xpath='descendant-or-self::a' data='<a href="/" class="Burger__right-arrow j'>,
<Selector xpath='descendant-or-self::a' data='<a href="/" class="Burger__right-arrow j'>,
<Selector xpath='descendant-or-self::a' data='<a href="#" class="js-dropdown Burger__r'>,
<Selector xpath='descendant-or-self::a' data='<a href="/mouvement-des-gilets-jaunes/" '>,
<Selector xpath='descendant-or-self::a' data='<a href="/carlos-ghosn/" data-suggestion'>,
<Selector xpath='descendant-or-self::a' data='<a href="/implant-files/" data-suggestio'>]

Pour récupérer le texte contenu dans les balises, on passe le paramètre
`<TAG>::text`. Par exemple :

In [ ]:
In [6]: response.css("title::text")
Out[6]: [<Selector xpath='descendant-or-self::title/text()' data='Le Monde.fr - Actualités et Infos en Fra'>]

### Exercice

  Comparer les résultats des deux requêtes `response.css('title')` et
`response.css('title::text')`.
=> On a enlever les balises. On ne garde que le contenu

Maintenant pour extraire les données des selecteurs on utilise l'une des
deux méthodes suivantes : - `extract()` permet de récupérer une liste
des données extraites de tous les sélecteurs - `extract_first()` permet
de récupérer une `String` provenant du premier sélecteur de la liste.

In [ ]:
In [7]: response.css('title::text').extract_first()
Out[7]: 'Le Monde.fr - Actualités et Infos en France et dans le monde'

On peut récupérer un attribut d'une balise avec la syntaxe
`<TAG>::attr(<ATTRIBUTE_NAME>)` :

Par exemple, les liens sont contenus dans un attribut `href`.

In [ ]:
In [9]: response.css('a::attr(href)')[0:10]
Out[9]:
[<Selector xpath='descendant-or-self::a/@href' data='https://journal.lemonde.fr'>,
<Selector xpath='descendant-or-self::a/@href' data='/'>,
<Selector xpath='descendant-or-self::a/@href' data='https://secure.lemonde.fr/sfuser/connexi'>,
<Selector xpath='descendant-or-self::a/@href' data='https://abo.lemonde.fr/#xtor=CS1-454[CTA'>,
<Selector xpath='descendant-or-self::a/@href' data='/'>,
<Selector xpath='descendant-or-self::a/@href' data='/'>,
<Selector xpath='descendant-or-self::a/@href' data='#'>,
<Selector xpath='descendant-or-self::a/@href' data='/mouvement-des-gilets-jaunes/'>,
<Selector xpath='descendant-or-self::a/@href' data='/carlos-ghosn/'>,
<Selector xpath='descendant-or-self::a/@href' data='/implant-files/'>]

Comme vu précédemment, si on veut récupérer la liste des liens de la page on applique la méthode $extract()$

In [ ]:
In [11]: response.css('a::attr(href)').extract()[0:10]
Out[11]:
['https://journal.lemonde.fr',
'/',
'https://secure.lemonde.fr/sfuser/connexion',
'https://abo.lemonde.fr/#xtor=CS1-454[CTA_LMFR]-[HEADER]-5-[Home]',
'/',
'/',
'#',
'/mouvement-des-gilets-jaunes/',
'/carlos-ghosn/',
'/implant-files/']

Les liens dans une page HTML sont souvent codés de manière relative par
rapport à la page courante. La méthode de l'objet `Response` peut être
utilisée pour recréer l'url complet.

Un exemple sur le 4e élément :

In [ ]:
In [14]: response.urljoin(response.css('a::attr(href)').extract()[8])
Out[14]: 'https://www.lemonde.fr/carlos-ghosn/'

alors que

In [ ]:
In [15]: response.css('a::attr(href)').extract()[8]
Out[15]: '/carlos-ghosn/'

### Exercice : 

Utiliser une liste compréhension pour transformer les 10
premiers liens relatifs récupérés par la méthode `extract()` en liens
absolus.    

Le résultat doit ressembler à :

In [ ]:
Out[23]: 
['https://journal.lemonde.fr',
'https://www.lemonde.fr/',
'https://secure.lemonde.fr/sfuser/connexion',
'https://abo.lemonde.fr/#xtor=CS1-454[CTA_LMFR]-[HEADER]-5-[Home]',
'https://www.lemonde.fr/',
'https://www.lemonde.fr/',
'https://www.lemonde.fr/',
'https://www.lemonde.fr/mouvement-des-gilets-jaunes/',
'https://www.lemonde.fr/carlos-ghosn/',
'https://www.lemonde.fr/implant-files/']

In [ ]:
[ response.urljoin(url) for url in response.css('a::attr(href)').extract()[0:10] ]

## Des requêtes plus complexes

On peut créer des requêtes plus complexes en utilisant à la fois la
structuration HTML du document mais également la couche de présentation
CSS. On utilise l'inspecteur de `Google Chrome` pour identifier le type
et l'identifiant de la balise contenant les informations.

Il y a au moins deux choses à savoir en `css` :  

-   Les `.` représentent les classes
-   Les `#` représentent les id

On se propose de récupérer toutes les sous-catégories de news dans la
catégorie **Actualités**. On remarque en utilisant l'inspecteur
d'élement de Chrome que toutes les catégories sont rangées dans une
balise avec l'id $#nav-markup$ ensuite dans les classes $Nav__item$.

A partir de cette structure HTML on peut construire la requête suivante
pour récupérer la barre de navigation:

In [ ]:
In [19]: response.css("#nav-markup")
Out[19]: [<Selector xpath="descendant-or-self::*[@id = 'nav-markup']" data='<ul id="nav-markup"> <li class="Nav__ite'>]

Ensuite pour récupérer les différentes catégories :

In [ ]:
In [24]: response.css("#nav-markup .Nav__item")
Out[24]:
[<Selector xpath="descendant-or-self::*[@id = 'nav-markup']/descendant-or-self::*/*[@class and contains(concat(' ', normalize-space(@class), ' '), ' Nav__item ')]" data='<li class="Nav__item js-burger-to-show N'>,
<Selector xpath="descendant-or-self::*[@id = 'nav-markup']/descendant-or-self::*/*[@class and contains(concat(' ', normalize-space(@class), ' '), ' Nav__item ')]" data='<li class="Nav__item Nav__item--home Nav'>,
<Selector xpath="descendant-or-self::*[@id = 'nav-markup']/descendant-or-self::*/*[@class and contains(concat(' ', normalize-space(@class), ' '), ' Nav__item ')]" data='<li class="Nav__item"> <a href="/" class'>,
<Selector xpath="descendant-or-self::*[@id = 'nav-markup']/descendant-or-self::*/*[@class and contains(concat(' ', normalize-space(@class), ' '), ' Nav__item ')]" data='<li class="Nav__item"> <a href="#" class'>,
<Selector xpath="descendant-or-self::*[@id = 'nav-markup']/descendant-or-self::*/*[@class and contains(concat(' ', normalize-space(@class), ' '), ' Nav__item ')]" data='<li class="Nav__item"> <a href="#" class'>,
<Selector xpath="descendant-or-self::*[@id = 'nav-markup']/descendant-or-self::*/*[@class and contains(concat(' ', normalize-space(@class), ' '), ' Nav__item ')]" data='<li class="Nav__item"> <a href="#" class'>,
<Selector xpath="descendant-or-self::*[@id = 'nav-markup']/descendant-or-self::*/*[@class and contains(concat(' ', normalize-space(@class), ' '), ' Nav__item ')]" data='<li class="Nav__item"> <a href="#" class'>,
<Selector xpath="descendant-or-self::*[@id = 'nav-markup']/descendant-or-self::*/*[@class and contains(concat(' ', normalize-space(@class), ' '), ' Nav__item ')]" data='<li class="Nav__item"> <a href="#" class'>,
<Selector xpath="descendant-or-self::*[@id = 'nav-markup']/descendant-or-self::*/*[@class and contains(concat(' ', normalize-space(@class), ' '), ' Nav__item ')]" data='<li class="Nav__item"> <a href="#" class'>,
<Selector xpath="descendant-or-self::*[@id = 'nav-markup']/descendant-or-self::*/*[@class and contains(concat(' ', normalize-space(@class), ' '), ' Nav__item ')]" data='<li class="Nav__item"> <a href="#" class'>,
<Selector xpath="descendant-or-self::*[@id = 'nav-markup']/descendant-or-self::*/*[@class and contains(concat(' ', normalize-space(@class), ' '), ' Nav__item ')]" data='<li class="Nav__item"> <a href="/recherc'>]

On veut maintenant retourner tous les liens présents dans cette
catégorie. On remarque qu'elle apparait à la 4eme position.

In [ ]:
In [34]: response.css("#nav-markup .Nav__item")[3]
Out[34]: <Selector xpath="descendant-or-self::*[@id = 'nav-markup']/descendant-or-self::*/*[@class and contains(concat(' ', normalize-space(@class), ' '), ' Nav__item ')]" data='<li class="Nav__item"> <a href="#" class'>

Maintenant pour récupérer tous les liens on peut chainer les requêtes.
On accède alors à toutes les balises $a$.

In [ ]:
In [35]: response.css("#nav-markup .Nav__item")[3].css("a")
Out[35]:
[<Selector xpath='descendant-or-self::a' data='<a href="#" class="js-dropdown Burger__r'>,
<Selector xpath='descendant-or-self::a' data='<a href="/mouvement-des-gilets-jaunes/" '>,
<Selector xpath='descendant-or-self::a' data='<a href="/carlos-ghosn/" data-suggestion'>,
<Selector xpath='descendant-or-self::a' data='<a href="/implant-files/" data-suggestio'>,
<Selector xpath='descendant-or-self::a' data='<a href="/climat/" data-suggestion>Clima'>,
<Selector xpath='descendant-or-self::a' data='<a href="/affaire-khashoggi/" data-sugge'>,
<Selector xpath='descendant-or-self::a' data='<a href="/emmanuel-macron/" data-suggest'>,
<Selector xpath='descendant-or-self::a' data='<a href="/ukraine/" data-suggestion>Ukra'>,
<Selector xpath='descendant-or-self::a' data='<a href="/russie/" data-suggestion>Russi'>,
<Selector xpath='descendant-or-self::a' data='<a href="/referendum-sur-le-brexit/" dat'>,
<Selector xpath='descendant-or-self::a' data='<a href="/harcelement-sexuel/" data-sugg'>,
<Selector xpath='descendant-or-self::a' data='<a href="/actualite-en-continu/" data-su'>,
<Selector xpath='descendant-or-self::a' data='<a href="/international/">International<'>,
<Selector xpath='descendant-or-self::a' data='<a href="/politique/">Politique</a>'>,
<Selector xpath='descendant-or-self::a' data='<a href="/societe/">Société</a>'>,
<Selector xpath='descendant-or-self::a' data='<a href="/les-decodeurs/">Les Décodeurs<'>,
<Selector xpath='descendant-or-self::a' data='<a href="/sport/">Sport</a>'>,
<Selector xpath='descendant-or-self::a' data='<a href="/planete/">Planète</a>'>,
<Selector xpath='descendant-or-self::a' data='<a href="/sciences/">Sciences</a>'>,
<Selector xpath='descendant-or-self::a' data='<a href="/campus/">M Campus</a>'>,
<Selector xpath='descendant-or-self::a' data='<a href="/afrique/">Le Monde Afrique</a>'>,
<Selector xpath='descendant-or-self::a' data='<a href="/pixels/">Pixels</a>'>,
<Selector xpath='descendant-or-self::a' data='<a href="/actualite-medias/">Médias</a>'>,
<Selector xpath='descendant-or-self::a' data='<a href="/sante/">Santé</a>'>,
<Selector xpath='descendant-or-self::a' data='<a href="/big-browser/">Big Browser</a>'>,
<Selector xpath='descendant-or-self::a' data='<a href="/disparitions/">Disparitions</a'>]

Et pour récupérer les titres :

In [ ]:
In [37]: response.css("#nav-markup .Nav__item")[3].css("a::text").extract()
Out[37]:
['Actualités',
'Mouvement des "gilets jaunes"',
'Carlos Ghosn',
'Implant Files',
'Climat',
'Affaire Khashoggi',
'Emmanuel Macron',
'Ukraine',
'Russie',
'Brexit',
'Harcèlement sexuel',
'Toute l’actualité en continu',
'International',
'Politique',
'Société',
'Les Décodeurs',
'Sport',
'Planète',
'Sciences',
'M Campus',
'Le Monde Afrique',
'Pixels',
'Médias',
'Santé',
'Big Browser',
'Disparitions']

In [ ]:
response.css("#nav-markup .Nav__item")[3].css("a::attr(href)").extract()

Le shell Scrapy permet de définir la structure des requêtes et de
s'assurer de la pertinence du résultat retourné. Pour automatiser le
processus, il faut intégrer cette syntaxe au code Python des modules de
spider définis dans la structure du projet.

## Intégration des requêtes

Le squelette de la classe `LeMondeSpider` généré lors de la création du
projet doit maintenant être enrichi. Par défaut 3 attributs et une
méthode `parse()` ont été créés :

-   `name` permet d'identifier sans ambiguïté la spider dans le code.
-   `allowed_domain` permet de filtrer les requêtes et forcer la spider
    à rester sur une liste de domaines.
-   `starts_urls` est la liste des urls d'où la spider va partir pour
    commencer son scraping.
-   `parse()` est une méthode héritée de la classe `scrapy.Spider`. Elle
    doit être redéfinie selon les requêtes que l'on doit effectuer et
    sera appelée sur l'ensemble des urls contenus dans la liste
    `starts_urls`.

`parse()` est une fonction `callback` qui sera appelée automatiquement
sur chaque objet `Response` retourné par la requête. Cette fonction est
appelée de manière asynchrone. Plusieurs requêtes peuvent ainsi être
lancées en parallèles sans bloquer le thread principal. L'objet
`Response` passé en paramètre est le même que celui mis à disposition
lors de l'exécution du Scrapy Shell.

In [ ]:
def parse(self, response):
    title = response.css('title::text').extract_first()
    all_links = {
        name:response.urljoin(url) for name, url in zip(
        response.css("#nav-markup .Nav__item")[3].css("a::text").extract(),
        response.css("#nav-markup .Nav__item")[3].css("a::attr(href)").extract())
    }
    yield {
        "title":title,
        "all_links":all_links
    }

La fonction est un générateur (`yield`) et retourne un dictionnaire
composé de deux éléments :

-   Le titre de la page;
-   La liste des liens sortants sous forme de String.

Pour le moment cette spider ne parcourt que la page d'accueil, ce qui
n'est pas très productif.

## Votre premier scraper

Récupérer les données sur un ensemble de pages webs nécessite d'explorer
en profondeur la structure du site en suivant tout ou partie des liens
rencontrés.

La spider peut se `balader` sur un site assez efficacement. Il suffit de
lui indiquer comment faire. Il faut spécifier à Scrapy de générer une
requête vers une nouvelle page en construisant l'objet `Request`
correspondant. Ce nouvel objet `Request` est alors inséré dans le
scheduler de Scrapy. On peut évidemment générer plusieurs `Request`
simultanément, correspondant par exemple, à différents liens sur la page
courante. Ils sont insérés séquentiellement dans le scheduler.

Pour cela on modifie la méthode `parse()` de façon à ce qu'elle retourne
un objet `Request` pour chaque nouveau lien rencontré. On associe
également à cet objet une fonction de callback qui déterminera la
manière dont cette nouvelle page doit être extraite.

Par exemple, pour que la spider continue dans les liens des différentes
régions (pour l'instant la fonction de callback ne fait rien) :

In [ ]:
# %load newscrawler/newscrawler/spiders/lemonde_v2.py
import scrapy
from scrapy import Request


class LemondeSpider(scrapy.Spider):
    name = "lemondev2"
    allowed_domains = ["www.lemonde.fr"]
    start_urls = ['https://www.lemonde.fr']

    def parse(self, response):
        title = response.css('title::text').extract_first()
        all_links = {
            name:response.urljoin(url) for name, url in zip(
            response.css("#nav-markup .Nav__item")[3].css("a::text").extract(),
            response.css("#nav-markup .Nav__item")[3].css("a::attr(href)").extract())
        }
        yield {
            "title":title,
            "all_links":all_links
        }
        

Pour lancer la spider

In [12]:
!cd newscrawler

In [13]:
!pwd

/home/dev/code/2Scrapy


In [16]:
!cd newscrawler && scrapy crawl lemondev2

2021-11-30 13:07:10 [scrapy.utils.log] INFO: Scrapy 2.4.0 started (bot: newscrawler)
2021-11-30 13:07:10 [scrapy.utils.log] INFO: Versions: lxml 4.6.4.0, libxml2 2.9.10, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 20.3.0, Python 3.8.12 (default, Nov 17 2021, 16:58:51) - [GCC 10.2.1 20210110], pyOpenSSL 19.1.0 (OpenSSL 1.1.1h  22 Sep 2020), cryptography 3.2.1, Platform Linux-5.10.16.3-microsoft-standard-WSL2-x86_64-with-glibc2.2.5
2021-11-30 13:07:10 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.epollreactor.EPollReactor
2021-11-30 13:07:10 [scrapy.crawler] INFO: Overridden settings:
{'BOT_NAME': 'newscrawler',
 'NEWSPIDER_MODULE': 'newscrawler.spiders',
 'ROBOTSTXT_OBEY': True,
 'SPIDER_MODULES': ['newscrawler.spiders']}
2021-11-30 13:07:10 [scrapy.extensions.telnet] INFO: Telnet Password: a5337774e6312f5a
2021-11-30 13:07:10 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.e

On veut ensuite *entrer* dans les liens des différentes sous-catégories
pour récupérer les articles. Pour cela, nous créons une méthode
`parse_category()` prend en argument un objet `Response` qui sera la
réponse correspondant aux liens des régions. On peut comme ceci
traverser un site en définissant des méthodes différentes en fonction du
type de contenu.

Si la structure du site est plus profonde, on peut empiler autant de
couches que souhaité.

Quand on arrive sur une page d'une sous-catégorie, on peut vouloir
récupérer tous les éléments de la page. Pour cela, on réutilise le
scrapy Shell pour commencer le développement de la nouvelle méthode
d'extraction.

Par exemple pour la page `https://www.lemonde.fr/international/` :

In [ ]:
scrapy shell 'https://www.lemonde.fr/international/'

Le fil des articles est stocké dans une balise avec la classe
`class=river`.

In [ ]:
In [3]: response.css(".river")
Out[3]:
[<Selector xpath="descendant-or-self::*[@class and contains(concat(' ', normalize-space(@class), ' '), ' fleuve ')]" data='<div class="fleuve">\n   <section>\n      '>,
<Selector xpath="descendant-or-self::*[@class and contains(concat(' ', normalize-space(@class), ' '), ' fleuve ')]" data='<div class="fleuve">\n</div>'>]

Pour récupérer chacun des articles, il faut adresser les balises
`.teaser` contenues dans le sélecteur:

In [ ]:
In [4]: response.css(".river")[0].css(".teaser")
Out[4]:
[<Selector xpath='descendant-or-self::article' data='<article class="grid_12 alpha enrichi mg'>,
<Selector xpath='descendant-or-self::article' data='<article class="grid_12 alpha enrichi">\n'>,
<Selector xpath='descendant-or-self::article' data='<article class="grid_12 alpha enrichi">\n'>,
<Selector xpath='descendant-or-self::article' data='<article class="grid_12 alpha enrichi">\n'>,
<Selector xpath='descendant-or-self::article' data='<article class="grid_12 alpha enrichi">\n'>,
<Selector xpath='descendant-or-self::article' data='<article class="grid_12 alpha enrichi">\n'>,
<Selector xpath='descendant-or-self::article' data='<article class="grid_12 alpha enrichi">\n'>,
<Selector xpath='descendant-or-self::article' data='<article class="grid_12 alpha enrichi">\n'>]   

Comme précédemment, on peut empiler les sélecteurs `css` pour créer des
requêtes plus complexes.

Par exemple, pour récupérer tous les titres des différents articles :

In [ ]:
In [8]: response.css(".river")[0].css(".teaser h3::text").extract()
Out[8]:
['Des dizaines de milliers de Géorgiens contestent dans la rue l’élection de Salomé Zourabichvili\r\n\r\n\r\n',
'A Budapest en Hongrie, un îlot décroissant pour favoriser la transition\r\n\r\n\r\n',
'En Israël, la police recommande l’inculpation de Nétanyahou dans une troisième enquête\r\n\r\n\r\n',
'Donald Trump veut «\xa0mettre fin\xa0» à l’Aléna rapidement\r\n\r\n\r\n',
'Le cauchemar de la «\xa0rééducation\xa0» des musulmans en Chine\r\n\r\n',
'\r\n',
'«\xa0AMLO\xa0» lance sa transformation du Mexique\r\n\r\n\r\n',
'«\xa0Paris brûle\xa0»\xa0: les médias étrangers relatent le «\xa0chaos\xa0» en marge des défilés des «\xa0gilets jaunes\xa0»\r\n\r\n\r\n',
'Andrés Manuel Lopez Obrador intronisé président du Mexique\r\n\r\n\r\n']

En HTML les données sont souvent de très mauvaise qualité. Il faut
définir des méthodes permettant de les nettoyer pour être intégrées dans
des bases de données.

Par exemple, pour supprimer tous les espaces superflus :

In [10]:
def clean_spaces(string_):
    if string_ is not None: 
        return " ".join(string_.split())

Pour l'appliquer à tous les titres récupérés, on peut faire une list
comprehension : 

In [ ]:
In [11]: [clean_spaces(article) for article in response.css(".river")[0].css(".teaser h3::text").extract()]  

Out[11]: ['Des dizaines de milliers de Géorgiens contestent dans la rue l’élection de Salomé Zourabichvili',
          'A Budapest en Hongrie, un îlot décroissant pour favoriser la transition', 
          'En Israël, la police recommande l’inculpation de Nétanyahou dans une troisième enquête',
          'Donald Trump veut « mettre fin » à l’Aléna rapidement', 
          'Le cauchemar de la « rééducation » des musulmans en Chine',
          '',
          '« AMLO » lance sa transformation du Mexique', 
          '« Paris brûle » : les médias étrangers relatent le « chaos » en marge des défilés des « gilets jaunes »',
          'Andrés Manuel Lopez Obrador intronisé président du Mexique'
         ]


La méthode précédente est intéressante si l'on ne recherche qu'une seule
information par article.

Par contre si l'on veut récupérer d'autres caractéristiques comme
l'image ou la description par exemple, il est plus intéressant et plus
efficace de récupérer l'objet et d'effectuer plusieurs traitements sur
ce dernier.

Chaque objet retourné par les requêtes `css` est un selecteur avec
lequel on peut interagir.

Par exemple pour récupérer le titre et le prix

In [ ]:
In [25]: for article in response.css(".fleuve")[0].css("article"):
...:     title = clean_spaces(article.css("h3 a::text").extract_first())
...:     image = article.css("img::attr(data-src)").extract_first()
...:     description = article.css(".txt3::text").extract_first()
...:     print(f"Title {title} \nImage {image}\nDescription {description}\n ----")


In [ ]:
Title Des dizaines de milliers de Géorgiens contestent dans la rue l’élection de Salomé Zourabichvili
Image https://s1.lemde.fr/image/2018/12/02/147x97/5391641_7_5874_les-partisans-de-l-opposant-grigol-vashadze_20d2e8693a49b83fd3c5578f7799ae9c.jpg
Description Elue présidente (un rôle essentiellement symbolique en Géorgie), l’ex-diplomate française, candidate du pouvoir, est contestée par l’opposition.
----
Title A Budapest en Hongrie, un îlot décroissant pour favoriser la transition
Image https://img.lemde.fr/2018/12/01/10/0/4214/2809/147/97/60/0/15b32ca_1EY4qISQ_BP4kPAh1fozJdXZ.jpg
Description Le centre logistique Cargonomia sert de matrice aux coopératives de l’économie durable et solidaire hongroise.
----
Title En Israël, la police recommande l’inculpation de Nétanyahou dans une troisième enquête
Image https://img.lemde.fr/2018/12/02/167/0/4207/2804/147/97/60/0/9e02c9b_3580d043ebc94b48b0f2cfef4e9a21e7-3580d043ebc94b48b0f2cfef4e9a21e7-0.jpg
Description Le premier ministre est soupçonné de corruption, fraude et abus de pouvoir, dans une affaire impliquant le groupe de télécoms israélien Bezeq.
----
Title Donald Trump veut « mettre fin » à l’Aléna rapidement
Image https://img.lemde.fr/2018/11/30/0/0/4861/3240/147/97/60/0/8b87184_5826023-01-06.jpg
Description Le président américain souhaite voir disparaître l’accord de libre-échange remontant à 1994 avec le Mexique et le Canada, qu’il qualifie régulièrement de « pire accord jamais signé », en faveur du nouveau traité négocié difficilement avec ses voisins nord-américains ces derniers mois.
----
Title Le cauchemar de la « rééducation » des musulmans en Chine
Image https://img.lemde.fr/2018/11/15/151/0/5000/3333/147/97/60/0/118c78f_248b226e6b91450aa8a68bd0ea5525a8-248b226e6b91450aa8a68bd0ea5525a8-0.jpg
Description Ouïgours et Kazakhs du Xinjiang... C’est toute une population musulmane que Pékin veut « rééduquer » en internant des centaines de milliers d’entre eux dans des camps.
----
Title « AMLO » lance sa transformation du Mexique
Image https://img.lemde.fr/2018/12/02/45/0/1497/998/147/97/60/0/a33c174_GGGTBR84_MEXICO-POLITICS-_1202_11.JPG
Description Education et santé gratuites, hausse du salaire minimum, bourses scolaires : à peine investi, le président Andres Manuel Lopez Obrador a listé les mesures qu’il entend prendre pour redresser le pays.
----
Title « Paris brûle » : les médias étrangers relatent le « chaos » en marge des défilés des « gilets jaunes »
Image https://img.lemde.fr/2018/12/02/361/0/598/396/147/97/60/0/ba46a6e_XVIt1Ffwm50iYBheccVieUQQ.jpg
Description Les images de destructions, d’échauffourées ou de voitures enflammées s’affichaient samedi soir en « une » de nombreux sites d’actualité internationaux.
----
Title Andrés Manuel Lopez Obrador intronisé président du Mexique
Image https://img.lemde.fr/2018/12/02/91/145/1346/897/147/97/60/0/877cd51_a4618baa8da2414bb62bab28a6d4c745-a4618baa8da2414bb62bab28a6d4c745-0.jpg
Description Le nouveau chef d’Etat a promis de lutter contre la corruption en menant une transformation « profonde et radicale » du pays.
----

## Persistence des données

Pour pouvoir stocker les informations que l'on récupère en parcourant un
site il faut pouvoir les stocker. On utilise soit de simples
dictionnaires Python, ou mieux des `scrapy.Item` qui sont des
dictionnaires améliorés.

Nous allons voir les deux façons de faire. On peut réécrire la méthode
`parse_category()` pour lui faire retourner un dictionnaire
correspondant à chaque offre rencontrée.

In [11]:
def parse_category(self, response):
    for article in response.css(".fleuve")[0].css("article"):
        title = self.clean_spaces(article.css("h3 a::text").extract_first())
        image = article.css("img::attr(data-src)").extract_first()
        description = article.css(".txt3::text").extract_first()
        yield {
            "title":title,
            "image":image,
            "description":description
        }

Si on combine tout dans la spider :

In [ ]:
# %load newscrawler/newscrawler/spiders/lemonde_v3.py
import scrapy
from scrapy import Request


class LemondeSpider(scrapy.Spider):
    name = "lemondev3"
    allowed_domains = ["www.lemonde.fr"]
    start_urls = ['https://www.lemonde.fr']

    def parse(self, response):
        title = response.css('title::text').extract_first()
        all_links = {
            name:response.urljoin(url) for name, url in zip(
            response.css("#nav-markup .Nav__item")[3].css("a::text").extract(),
            response.css("#nav-markup .Nav__item")[3].css("a::attr(href)").extract())
        }
        for link in all_links.values():
            yield Request(link, callback=self.parse_category)
            
    def parse_category(self, response):
        for article in response.css(".river")[0].css(".teaser"):
            title = self.clean_spaces(article.css("h3::text").extract_first())
            image = article.css("img::attr(data-src)").extract_first()
            description = article.css(".txt3::text").extract_first()
            yield {
                "title":title,
                "image":image,
                "description":description
            }

    def clean_spaces(self, string):
        if string:
            return " ".join(string.split())

On peut maintenant lancer notre spider avec la commande suivante :

In [ ]:
scrapy crawl <NAME>

`scrapy crawl` permet de démarrer le processus en allant chercher la
classe `scrapy.Spider` dont l'attribut `name` = &lt;NAME&gt;.

Par exemple, pour la spider `LeMondeSpider` :

In [20]:
!cd newscrawler && scrapy crawl lemondev3 -o lbc.json

2021-11-30 13:23:00 [scrapy.utils.log] INFO: Scrapy 2.4.0 started (bot: newscrawler)
2021-11-30 13:23:00 [scrapy.utils.log] INFO: Versions: lxml 4.6.4.0, libxml2 2.9.10, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 20.3.0, Python 3.8.12 (default, Nov 17 2021, 16:58:51) - [GCC 10.2.1 20210110], pyOpenSSL 19.1.0 (OpenSSL 1.1.1h  22 Sep 2020), cryptography 3.2.1, Platform Linux-5.10.16.3-microsoft-standard-WSL2-x86_64-with-glibc2.2.5
2021-11-30 13:23:00 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.epollreactor.EPollReactor
2021-11-30 13:23:00 [scrapy.crawler] INFO: Overridden settings:
{'BOT_NAME': 'newscrawler',
 'NEWSPIDER_MODULE': 'newscrawler.spiders',
 'ROBOTSTXT_OBEY': True,
 'SPIDER_MODULES': ['newscrawler.spiders']}
2021-11-30 13:23:00 [scrapy.extensions.telnet] INFO: Telnet Password: ae2e47db36c348c7
2021-11-30 13:23:00 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.e

2021-11-30 13:23:01 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/le-monde-et-vous/> (referer: https://www.lemonde.fr)
2021-11-30 13:23:01 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/pixels/> (referer: https://www.lemonde.fr)
2021-11-30 13:23:01 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/afrique/> (referer: https://www.lemonde.fr)
2021-11-30 13:23:01 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/podcasts/> (referer: https://www.lemonde.fr)
2021-11-30 13:23:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/campus/>
{'title': '« Les hommes sages-femmes sont surreprésentés dans les postes valorisés »', 'image': 'https://img.lemde.fr/2021/09/25/0/0/3504/2336/110/74/60/0/e0e1a5f_420864799-sagesfemmes.jpg', 'description': 'S’ils restent minoritaires dans la profession, les hommes sont plus nombreux dans les emplois de cadres, enseignants ou dirigeants d’instances syndic

2021-11-30 13:23:01 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/sciences/> (referer: https://www.lemonde.fr)
2021-11-30 13:23:01 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/sport/> (referer: https://www.lemonde.fr)
2021-11-30 13:23:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/campus/>
{'title': 'Arthur Nauzyciel : « Beaucoup de jeunes veulent se rassurer avec un diplôme, mais je trouve que cela les formate »', 'image': 'https://img.lemde.fr/2021/11/18/116/0/2277/1518/110/74/60/0/0d261ec_275059453-arthur-nauzyciel-louise-quignon.jpg', 'description': 'L’émission «\xa0Le Monde Campus Le Mag’\xa0» fait étape à Rennes. Rencontre en première partie avec le comédien, metteur en scène et directeur du TNB Arthur Nauzyciel. Le parrain de l’émission revient sur son parcours.'}
2021-11-30 13:23:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/campus/>
{'title': '« En être ou ne pas en être » : l

2021-11-30 13:23:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/big-browser/>
{'title': 'Une marionnette asiatique dans la légendaire émission américaine « Sesame Street »', 'image': 'https://img.lemde.fr/2021/11/15/0/0/5472/3648/110/74/60/0/caba880_a63332225b7d481b97c9c48bb0961451-a63332225b7d481b97c9c48bb0961451-0.jpg', 'description': 'Ji-Young, marionnette américaine d’origine coréenne, va lutter contre les préjugés croissants dont sont victimes les Américains d’origines asiatiques.'}
2021-11-30 13:23:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/campus/>
{'title': 'Succession à Sciences Po : Mathias Vicherat adoubé par un premier vote du conseil de l’Institut', 'image': 'https://img.lemde.fr/2017/01/10/176/58/741/494/110/74/60/0/0f61551_17626-zz7lvk.hnwr4l5wmi.JPG', 'description': 'Le conseil de l’Institut a plébiscité la candidature de cet énarque face à celles des universitaires Christine Musselin et Olivier Faron. Un second vo

2021-11-30 13:23:01 [scrapy.core.scraper] ERROR: Spider error processing <GET https://www.lemonde.fr/le-monde-et-vous/> (referer: https://www.lemonde.fr)
Traceback (most recent call last):
  File "/root/.local/share/virtualenvs/code-AFz48Hjb/lib/python3.8/site-packages/scrapy/utils/defer.py", line 120, in iter_errback
    yield next(it)
  File "/root/.local/share/virtualenvs/code-AFz48Hjb/lib/python3.8/site-packages/scrapy/utils/python.py", line 353, in __next__
    return next(self.data)
  File "/root/.local/share/virtualenvs/code-AFz48Hjb/lib/python3.8/site-packages/scrapy/utils/python.py", line 353, in __next__
    return next(self.data)
  File "/root/.local/share/virtualenvs/code-AFz48Hjb/lib/python3.8/site-packages/scrapy/core/spidermw.py", line 62, in _evaluate_iterable
    for r in iterable:
  File "/root/.local/share/virtualenvs/code-AFz48Hjb/lib/python3.8/site-packages/scrapy/spidermiddlewares/offsite.py", line 29, in process_spider_output
    for x in result:
  File "/root/.l

...

2021-11-30 13:23:03 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/coronavirus-2019-ncov/>
{'title': 'Le président chinois promet à l’Afrique un milliard de doses anti-Covid', 'image': 'https://img.lemde.fr/2021/11/30/1/0/3600/2400/110/74/60/0/9ccc2a0_851272081-000-9tl6ze.jpg', 'description': 'Pékin a également annoncé des dizaines de projets dans les domaines de la santé, du numérique et de la sécurité, ainsi qu’une annulation de dette.'}
2021-11-30 13:23:03 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/coronavirus-2019-ncov/>
{'title': 'Le variant Omicron détecté pour la première fois en France, à La Réunion', 'image': 'https://img.lemde.fr/2021/11/30/0/0/7348/4899/110/74/60/0/7ffb873_568381245-000-9hk2j3.jpg', 'description': 'Le patient est un homme qui a voyagé au Mozambique et a fait escale en Afrique du Sud, le premier pays à avoir détecté Omicron. Il s’agirait du premier cas identifié en France de ce variant du coronavirus qui se ré

2021-11-30 13:23:03 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/proces-des-attentats-du-13-novembre/>
{'title': 'Procès des attentats du 13-Novembre : la parole à tous, mais dans quel ordre ?', 'image': 'https://img.lemde.fr/2021/09/10/17/0/3543/2362/110/74/60/0/f1450db_745661667-13-novembre-final.jpg', 'description': 'Le président de la cour a choisi d’inverser l’ordre des intervenants en donnant la primeur des interrogatoires aux représentants de l’accusation. Suivront les parties civiles et la défense, qui s’exprime traditionnellement en dernier.'}
2021-11-30 13:23:03 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/proces-des-attentats-du-13-novembre/>
{'title': '« Vingt ans de tâtonnements de l’injonction française à l’intégration séparent Khaled Kelkal et Salah Abdeslam »', 'image': 'https://img.lemde.fr/2021/09/10/0/0/5616/3744/110/74/60/0/46c0cc5_575730977-056071.jpg', 'description': 'Dans sa chronique, Philippe Bernard, éditoriali

2021-11-30 13:23:03 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/international/>
{'title': 'Menacé, le mythique quotidien polonais « Gazeta Wyborcza » lutte pour son identité', 'image': 'https://img.lemde.fr/2021/11/27/86/0/2048/1365/110/74/60/0/3d22515_365965000-1999-02-09t120000z-434096911-pbeahulwxah-rtrmadp-3-poland.JPG', 'description': 'Confrontés aux décisions d’un conseil d’administration hostile, les journalistes luttent pour préserver la spécificité du titre emblématique.'}
2021-11-30 13:23:03 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/international/>
{'title': 'Le vote pour l’extrême droite au Chili est « le signal d’un retour à l’ordre »', 'image': 'https://img.lemde.fr/2021/11/26/0/0/5760/3840/110/74/60/0/9264c74_10814511-649901.jpg', 'description': 'Pour la sociologue Stéphanie Alenda, le premier tour du scrutin présidentiel, qui a porté l’extrême droite en tête, exprime une réaction à la révolte sociale initiée en\xa0201

2021-11-30 13:23:03 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/vaccins-contre-le-covid-19/>
{'title': 'En Guadeloupe, la préfecture impose un couvre-feu au cinquième jour des manifestations contre le passe sanitaire', 'image': 'https://img.lemde.fr/2021/11/17/0/4/3745/2497/110/74/60/0/b88003a_5033843-01-06.jpg', 'description': 'La préfecture interdit la circulation dans le département entre\xa018\xa0heures et\xa05\xa0heures, dès vendredi soir, «\xa0compte tenu des mouvements sociaux en cours dans le département et des actes de vandalisme\xa0».'}
2021-11-30 13:23:03 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/vaccins-contre-le-covid-19/>
{'title': 'Vaccination contre le Covid-19 : les Etats-Unis autorisent une dose de rappel pour tous les adultes', 'image': 'https://img.lemde.fr/2021/11/19/0/3/4270/2847/110/74/60/0/726dedb_838822015-000-9ry6dt.jpg', 'description': 'Selon la décision des autorités sanitaires, un rappel est désormais po

2021-11-30 13:23:03 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/election-presidentielle-2022/>
{'title': 'Les ambitions de Bruno Le Maire, le converti de la Macronie', 'image': 'https://img.lemde.fr/2021/11/17/0/4/4351/2901/110/74/60/0/df31f35_869676662-000-9pm3mj.jpg', 'description': 'Désormais ministre de l’économie, des finances et de la relance, l’ancien transfuge a donné des gages de loyauté. Loin de perturber son ambition politique, la pandémie est venue la servir.'}
2021-11-30 13:23:03 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/coronavirus-2019-ncov/>
{'title': 'Le feu vert européen accélère les réflexions sur la vaccination des enfants contre le Covid-19', 'image': 'https://img.lemde.fr/2021/11/26/0/6/5926/3951/110/74/60/0/45ad924_431030055-653747.jpg', 'description': 'En France, la Haute Autorité de santé devrait bientôt se prononcer sur ce sujet sensible. Si sa recommandation est positive, le gouvernement pourrait ouvrir la

On peut exporter les résultats de ces retours dans différents formats de
fichiers.

-   CSV : `scrapy crawl lemonde -o lbc.csv`
-   JSON : `scrapy crawl lemonde -o lbc.json`
-   JSONLINE : `scrapy crawl lemonde -o lbc.jl`
-   XML : `scrapy crawl lemonde -o lbc.xml`

### Exercice :

Exécuter la spider avec les différents formats de stockage.
Explorer ensuite le contenu des fichiers ainsi créés.

In [22]:
!cd newscrawler && scrapy crawl lemondev3 -o lbc.csv

2021-11-30 13:26:39 [scrapy.utils.log] INFO: Scrapy 2.4.0 started (bot: newscrawler)
2021-11-30 13:26:39 [scrapy.utils.log] INFO: Versions: lxml 4.6.4.0, libxml2 2.9.10, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 20.3.0, Python 3.8.12 (default, Nov 17 2021, 16:58:51) - [GCC 10.2.1 20210110], pyOpenSSL 19.1.0 (OpenSSL 1.1.1h  22 Sep 2020), cryptography 3.2.1, Platform Linux-5.10.16.3-microsoft-standard-WSL2-x86_64-with-glibc2.2.5
2021-11-30 13:26:39 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.epollreactor.EPollReactor
2021-11-30 13:26:39 [scrapy.crawler] INFO: Overridden settings:
{'BOT_NAME': 'newscrawler',
 'NEWSPIDER_MODULE': 'newscrawler.spiders',
 'ROBOTSTXT_OBEY': True,
 'SPIDER_MODULES': ['newscrawler.spiders']}
2021-11-30 13:26:39 [scrapy.extensions.telnet] INFO: Telnet Password: 102102bf95198102
2021-11-30 13:26:39 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.e

2021-11-30 13:26:42 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/campus/>
{'title': 'Une enquête alerte sur la santé mentale des étudiants et internes en médecine', 'image': 'https://img.lemde.fr/2021/10/28/0/0/6039/4026/110/74/60/0/d1996b2_648209973-210119jbalague-lemonde-covid-bichat-5y5a8964.jpg', 'description': 'Publiée mercredi, l’enquête révèle un grand mal-être et des conditions de travail déplorables : en période de stage, deux tiers d’entre eux ont fait un burn-out.'}
2021-11-30 13:26:42 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/campus/>
{'title': 'Dans les grandes écoles, des ateliers pour aider les femmes à mieux négocier leur salaire', 'image': 'https://img.lemde.fr/2021/10/21/778/0/4093/2728/110/74/60/0/f99fe3c_120578635-pns-3927011.jpg', 'description': 'Face aux écarts de rémunération persistants, des écoles ont mis en place des formations pour aider les femmes à mieux mettre en avant leurs compétences et déconstruire l

2021-11-30 13:26:42 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/sciences/> (referer: https://www.lemonde.fr)
2021-11-30 13:26:42 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/big-browser/> (referer: https://www.lemonde.fr)
2021-11-30 13:26:42 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/podcasts/> (referer: https://www.lemonde.fr)
2021-11-30 13:26:42 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/pixels/> (referer: https://www.lemonde.fr)
2021-11-30 13:26:42 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/le-monde-et-vous/> (referer: https://www.lemonde.fr)
2021-11-30 13:26:42 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/sante/> (referer: https://www.lemonde.fr)
2021-11-30 13:26:42 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/disparitions/> (referer: https://www.lemonde.fr)
2021-11-30 13:26:42 [scrapy.core.engine] DEBU

2021-11-30 13:26:42 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/big-browser/>
{'title': 'La justice américaine accorde des droits aux hippopotames de Pablo Escobar', 'image': 'https://img.lemde.fr/2021/10/25/0/136/3471/2314/110/74/60/0/8b6c8dd_cad0b60b73ba45f28821325dd9fcd602-cad0b60b73ba45f28821325dd9fcd602-0.jpg', 'description': 'Les animaux importés par le baron de la drogue ont donné naissance à une vaste colonie. La Colombie a décidé de les stériliser mais une cour américaine saisie par une association autorise les bêtes à recueillir l’avis de deux éminents vétérinaires.'}
2021-11-30 13:26:42 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/big-browser/>
{'title': 'Pour avoir sa statue à Londres, il vaut mieux être un animal qu’une femme admirable', 'image': 'https://img.lemde.fr/2021/10/27/152/1360/4224/2816/110/74/60/0/d28518b_124198777-000-dv1344004.jpg', 'description': 'L’immense majorité des quelque 1\xa0100 statues de la capital

2021-11-30 13:26:42 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/pixels/>
{'title': 'Un régulateur britannique ordonne à Facebook de vendre Giphy', 'image': 'https://img.lemde.fr/2021/11/18/0/144/3453/2302/110/74/60/0/1e470e2_846c296cb77d44f48a34177c63f2de8a-846c296cb77d44f48a34177c63f2de8a-0.jpg', 'description': 'Le mois dernier, le gendarme britannique de la concurrence avait infligé une amende de 50,5\xa0millions de livres au géant des réseaux sociaux dans le cadre de sa fusion avec Giphy, spécialisé dans les animations courtes sur Internet.'}
2021-11-30 13:26:42 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/big-browser/>
{'title': 'Une Médaille d’honneur pour le caporal Woodson : mobilisation pour récompenser à titre posthume un héros noir d’Omaha Beach', 'image': 'https://img.lemde.fr/2021/06/22/42/25/431/287/110/74/60/0/4d13ef0_461833109-woodson-portrait.jpg', 'description': 'Au sein de la seule formation de combat noire américaine

...

2021-11-30 13:26:44 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/coronavirus-2019-ncov/>
{'title': '« Grande Sécu » : « Les primes des complémentaires sont doublement inégalitaires, aux dépens des plus pauvres et des plus âgés »', 'image': 'https://img.lemde.fr/2021/11/26/0/0/5760/3840/110/74/60/0/f84bae0_99728504-pns-6307555.jpg', 'description': 'Le président du Syndicat des audioprothésistes, Luis Godinho, rappelle, dans une tribune au «\xa0Monde\xa0», que le système actuel d’articulation entre assurance-maladie et assurances-santé cache de forts écarts entre catégories d’usagers, et estime que le statu quo n’est pas tenable.'}
2021-11-30 13:26:44 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/immigration-en-europe/>
{'title': 'En Grèce, l’aide aux migrants criminalisée', 'image': 'https://img.lemde.fr/2021/11/22/0/0/3499/2333/110/74/60/0/aebaeb7_440340622-839246.jpg', 'description': 'Après le report de leur procès à Lesbos, 24 humanita

2021-11-30 13:26:44 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/vaccins-contre-le-covid-19/>
{'title': 'Covid-19 : en Grèce, les non-vaccinés font face à de nouvelles restrictions', 'image': 'https://img.lemde.fr/2021/11/19/0/0/8640/5760/110/74/60/0/a7811d0_840198606-192210.jpg', 'description': 'A partir du 22\xa0novembre, les non-vaccinés ne pourront plus entrer dans les espaces clos, comme les musées ou les salles de sport. L’accès aux restaurants ou aux églises leur reste autorisé, à condition de présenter des tests PCR ou antigéniques négatifs.'}
2021-11-30 13:26:44 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/vaccins-contre-le-covid-19/>
{'title': 'En rendant le vaccin contre le Covid-19 obligatoire pour toute la population, l’Autriche brise un tabou', 'image': 'https://img.lemde.fr/2021/11/19/133/0/6000/3994/110/74/60/0/9466ec8_711820587-613141.jpg', 'description': 'Le retour d’un confinement général dès le 22\xa0novembre et le c

2021-11-30 13:26:44 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/climat/>
{'title': 'Comment l’Homme modifie l’équilibre du climat sur la Terre', 'image': 'https://img.lemde.fr/2021/11/03/1192/483/3332/2221/110/74/60/0/840b2a0_184684508-000-9qn2f6.jpg', 'description': 'En 250\xa0ans, la Terre s’est réchauffée à un rythme jamais vu dans sa longue histoire. Progressivement, son système climatique est passé d’un équilibre à un déséquilibre.'}
2021-11-30 13:26:44 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/vaccins-contre-le-covid-19/>
{'title': 'Vaccination contre le Covid-19 : les Etats-Unis autorisent une dose de rappel pour tous les adultes', 'image': 'https://img.lemde.fr/2021/11/19/0/3/4270/2847/110/74/60/0/726dedb_838822015-000-9ry6dt.jpg', 'description': 'Selon la décision des autorités sanitaires, un rappel est désormais possible pour toutes les personnes de plus de 18\xa0ans et il est particulièrement recommandé à partir de 50\xa0

2021-11-30 13:26:44 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/bielorussie/>
{'title': 'L’opposante biélorusse Maria Kolesnikova récompensée par le prix Vaclav-Havel', 'image': 'https://img.lemde.fr/2021/09/06/0/0/3552/2368/110/74/60/0/d44169a_6fe9aededfc64eb98dc170c7c1a2a1f2-6fe9aededfc64eb98dc170c7c1a2a1f2-0.jpg', 'description': 'Elle est «\xa0l’un des trois symboles féminins de l’opposition biélorusse\xa0», a rappelé le Conseil de l’Europe, avec Svetlana Tikhanovskaïa, candidate à la présidentielle à la place de son mari emprisonné, et Veronika Tsepkalo, qui ont fui le pays sous la pression des autorités.'}
2021-11-30 13:26:44 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/bielorussie/>
{'title': 'A la frontière entre la Biélorussie et la Pologne, la crise migratoire fait ses premières victimes', 'image': 'https://img.lemde.fr/2021/09/23/0/0/3543/2362/110/74/60/0/4d2f2f9_945407256-090164.jpg', 'description': 'Quatre personnes, dont u

2021-11-30 13:26:44 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/immigration-en-europe/>
{'title': 'Migrants massés à la frontière par la Biélorussie : « Cette crise peut servir la Pologne dans ses contentieux avec l’UE »', 'image': 'https://img.lemde.fr/2021/11/10/0/0/3717/2478/110/74/60/0/b87033c_546b3e855ce748cdbf0b6c53f4f3607a-546b3e855ce748cdbf0b6c53f4f3607a-0.jpg', 'description': 'En jouant sur la peur d’un afflux massif de migrants, Varsovie veut pousser l’Union européenne à fermer les yeux sur ses entorses à l’Etat de droit, souligne le chercheur Matthieu Tardis, spécialiste de la politique européenne d’immigration.'}
2021-11-30 13:26:44 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/immigration-en-europe/>
{'title': 'La Biélorussie accusée d’instrumentaliser la crise des migrants par les Occidentaux à l’ONU', 'image': 'https://img.lemde.fr/2021/11/11/0/0/4005/2670/110/74/60/0/5e986c9_19e2d6c2abeb482b8dd2d446213cadc3-19e2d6c2abeb4

In [26]:
!cd newscrawler && scrapy crawl lemondev3 -o lbc.json

2021-11-30 13:27:43 [scrapy.utils.log] INFO: Scrapy 2.4.0 started (bot: newscrawler)
2021-11-30 13:27:43 [scrapy.utils.log] INFO: Versions: lxml 4.6.4.0, libxml2 2.9.10, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 20.3.0, Python 3.8.12 (default, Nov 17 2021, 16:58:51) - [GCC 10.2.1 20210110], pyOpenSSL 19.1.0 (OpenSSL 1.1.1h  22 Sep 2020), cryptography 3.2.1, Platform Linux-5.10.16.3-microsoft-standard-WSL2-x86_64-with-glibc2.2.5
2021-11-30 13:27:43 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.epollreactor.EPollReactor
2021-11-30 13:27:43 [scrapy.crawler] INFO: Overridden settings:
{'BOT_NAME': 'newscrawler',
 'NEWSPIDER_MODULE': 'newscrawler.spiders',
 'ROBOTSTXT_OBEY': True,
 'SPIDER_MODULES': ['newscrawler.spiders']}
2021-11-30 13:27:43 [scrapy.extensions.telnet] INFO: Telnet Password: 3d460fcde53920be
2021-11-30 13:27:43 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.e

2021-11-30 13:27:45 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/pixels/>
{'title': '« Le dark Net sert aussi à communiquer sans être repéré »', 'image': 'https://img.lemde.fr/2017/07/20/3/0/1737/1157/110/74/60/0/8cd7814_20424-1fa76tu.86znzv9529.png', 'description': 'La consultante Claire Gerardin défend, dans une tribune au «\xa0Monde\xa0», l’usage des réseaux anonymisés, trop souvent assimilés aux activités criminelles par les gouvernements et les géants du Web.'}
2021-11-30 13:27:45 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/pixels/>
{'title': '« Il faut obliger les plates-formes à respecter les grands principes de l’Etat de droit »', 'image': 'https://img.lemde.fr/2021/11/10/0/0/2025/1350/110/74/60/0/31fac70_5988299-01-06.jpg', 'description': 'Réguler le contenu des réseaux sociaux doit moins passer par la contrainte que par la préservation des droits individuels face aux géants du Web, estime le juriste Winston Maxwell dans une t

2021-11-30 13:27:45 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/podcasts/> (referer: https://www.lemonde.fr)
2021-11-30 13:27:46 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/disparitions/> (referer: https://www.lemonde.fr)
2021-11-30 13:27:46 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/campus/>
{'title': '« Les hommes sages-femmes sont surreprésentés dans les postes valorisés »', 'image': 'https://img.lemde.fr/2021/09/25/0/0/3504/2336/110/74/60/0/e0e1a5f_420864799-sagesfemmes.jpg', 'description': 'S’ils restent minoritaires dans la profession, les hommes sont plus nombreux dans les emplois de cadres, enseignants ou dirigeants d’instances syndicales, explique le sociologue Philippe Charrier dans un entretien au «\xa0Monde\xa0».'}
2021-11-30 13:27:46 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/campus/>
{'title': '« Les quotas dans les grandes écoles n’auront pas d’effet sur le phénomène

2021-11-30 13:27:46 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/campus/>
{'title': 'Violences sexuelles et sexistes : l’ENS de Lyon rappelée à l’ordre', 'image': 'https://img.lemde.fr/2021/10/28/378/0/768/511/110/74/60/0/3dabc1b_713638099-ens-lyon.jpg', 'description': 'L’inspection générale de l’éducation, du sport et de la recherche révèle qu’une seule procédure disciplinaire a été engagée sur quinze situations d’agression, de harcèlement ou de viol dont la direction de l’école avait connaissance.'}
2021-11-30 13:27:46 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/campus/>
{'title': 'Une enquête alerte sur la santé mentale des étudiants et internes en médecine', 'image': 'https://img.lemde.fr/2021/10/28/0/0/6039/4026/110/74/60/0/d1996b2_648209973-210119jbalague-lemonde-covid-bichat-5y5a8964.jpg', 'description': 'Publiée mercredi, l’enquête révèle un grand mal-être et des conditions de travail déplorables : en période de stage, deux tie

2021-11-30 13:27:46 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/planete/> (referer: https://www.lemonde.fr)
2021-11-30 13:27:46 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/campus/>
{'title': '« Au conservatoire, j’étais presque tout le temps quasi nue, à me faire palper de partout » : dans les écoles de théâtre, des élèves dénoncent une culture de la violence', 'image': 'https://img.lemde.fr/2021/10/25/0/0/7542/5024/110/74/60/0/2a18cca_967262567-violencestheatre-clr-01.jpeg', 'description': 'Des apprenties comédiennes racontent l’ambiance au sein de certains cours d’art dramatique, terrain propice à des abus de la part de certains professeurs et témoignent d’agressions sexuelles ou de viols.'}
2021-11-30 13:27:46 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/campus/>
{'title': 'Amours Bio, Bioflirt, GreenLovers… Le marché de la drague virtuelle s’adapte aux aspirations des jeunes écolos en quête d’amour', 'imag

...

2021-11-30 13:27:47 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/election-presidentielle-2022/>
{'title': 'Comparez les programmes des cinq prétendants à l’investiture des Républicains pour la présidentielle', 'image': 'https://img.lemde.fr/2021/11/30/283/0/6916/4610/110/74/60/0/63b7660_913407538-000-9rn49j.jpg', 'description': 'Retrouvez les principales propositions des cinq prétendants à l’investiture des Républicains pour l’élection présidentielle – Michel Barnier, Eric Ciotti, Valérie Pécresse, Philippe Juvin et Xavier Bertrand –, qui seront départagés lors du congrès du parti, qui aura lieu du 1er au 4\xa0décembre.'}
2021-11-30 13:27:47 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/election-presidentielle-2022/>
{'title': 'Yannick Jadot veut rassembler la gauche à la présidentielle, Anne Hidalgo répond que seule « la social-démocratie » peut y parvenir', 'image': 'https://img.lemde.fr/2021/11/18/0/0/3306/2204/110/74/60/0/7313b92_503

2021-11-30 13:27:47 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/immigration-en-europe/>
{'title': '« Les accords du Touquet permettent à Londres de se soustraire à son devoir d’asile. Le Brexit les a rendus obsolètes »', 'image': 'https://img.lemde.fr/2021/11/19/0/0/3543/2362/110/74/60/0/4190b51_901010080-08-calais-gratacap-271021.jpg', 'description': 'A l’heure où Calais est devenue une frontière extérieure de l’Union, la France serait fondée à dénoncer des accords qui en font l’otage des choix politiques du Royaume-Uni et maintiennent des milliers de migrants dans des conditions indignes, analyse Philippe Bernard, éditorialiste au «\xa0Monde\xa0», dans sa chronique.'}
2021-11-30 13:27:47 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/immigration-en-europe/>
{'title': 'La crise sanitaire a « significativement aggravé » la situation des réfugiés', 'image': 'https://img.lemde.fr/2021/11/05/0/0/5029/3353/110/74/60/0/c32988a_fdf23cb2b77b4d4

2021-11-30 13:27:47 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/election-presidentielle-2022/>
{'title': 'Présidentielle 2022 : les partis de gauche peinent à financer leur campagne', 'image': 'https://img.lemde.fr/2021/10/24/1/0/3898/2598/110/74/60/0/86efe8a_529845913-04.jpg', 'description': 'Les sondages peu optimistes n’encouragent à la dépense ni les banques ni les partis. Les socialistes revendiquent de faire une «\xa0campagne sobre\xa0».'}
2021-11-30 13:27:47 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/election-presidentielle-2022/>
{'title': 'Entre Emmanuel Macron et Xavier Bertrand, comme un avant-goût de débat présidentiel', 'image': 'https://img.lemde.fr/2021/11/19/0/0/3600/2400/110/74/60/0/d3009fe_656436556-macron-nord-aisne-32.jpg', 'description': 'En visite dans l’Aisne et le Nord, le chef de l’Etat a été pris à partie de manière virulente par le président des Hauts-de-France. Une manière pour ce dernier de se poser en pr

2021-11-30 13:27:47 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/proces-des-attentats-du-13-novembre/>
{'title': 'Au premier jour du procès des attentats du 13-Novembre, les provocations de Salah Abdeslam', 'image': 'https://img.lemde.fr/2021/09/09/293/320/4606/3071/110/74/60/0/6112df9_791224641-gr005.jpg', 'description': 'Le seul survivant des commandos s’est présenté comme un «\xa0combattant de l’Etat islamique\xa0». Il s’est également plaint de ses conditions de détention.'}
2021-11-30 13:27:47 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/proces-des-attentats-du-13-novembre/>
{'title': '« Les attentats du 13-Novembre sont le point d’orgue du djihadisme européen, qui s’est structuré à partir du 11-Septembre »', 'image': 'https://img.lemde.fr/2021/09/08/0/0/5342/3561/110/74/60/0/d964406_496355851-000-1at0pz.jpg', 'description': 'Le chercheur Hugo Micheron détaille, dans une tribune au «\xa0Monde\xa0», comment les attentats aux Etats-Un

2021-11-30 13:27:47 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/vaccins-contre-le-covid-19/>
{'title': 'Guadeloupe : la grève générale contre l’obligation vaccinale des soignants se poursuit sous tension', 'image': 'https://img.lemde.fr/2021/11/16/0/0/4816/3210/110/74/60/0/61b858e_800174170-guadeloupe.jpg', 'description': 'Une manifestation a rassemblé entre 300 et 400 personnes mardi devant le CHU de Pointe-à-Pitre, devant lequel s’est également terminée une opération escargot des pompiers.'}
2021-11-30 13:27:47 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/vaccins-contre-le-covid-19/>
{'title': 'Grève contre l’obligation vaccinale à la Guadeloupe : 2 pompiers blessés, 2 arrestations', 'image': 'https://img.lemde.fr/2021/11/16/0/0/4945/3297/110/74/60/0/33c4938_12143779-000-9kq9e8.jpg', 'description': 'Des échauffourées ont opposé, lundi, pompiers grévistes et gendarmes. Le parquet de Pointe-à-Pitre a fait savoir que deux personnes avai

In [24]:
!cd newscrawler && scrapy crawl lemondev3 -o lbc.jl

2021-11-30 13:26:54 [scrapy.utils.log] INFO: Scrapy 2.4.0 started (bot: newscrawler)
2021-11-30 13:26:54 [scrapy.utils.log] INFO: Versions: lxml 4.6.4.0, libxml2 2.9.10, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 20.3.0, Python 3.8.12 (default, Nov 17 2021, 16:58:51) - [GCC 10.2.1 20210110], pyOpenSSL 19.1.0 (OpenSSL 1.1.1h  22 Sep 2020), cryptography 3.2.1, Platform Linux-5.10.16.3-microsoft-standard-WSL2-x86_64-with-glibc2.2.5
2021-11-30 13:26:54 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.epollreactor.EPollReactor
2021-11-30 13:26:54 [scrapy.crawler] INFO: Overridden settings:
{'BOT_NAME': 'newscrawler',
 'NEWSPIDER_MODULE': 'newscrawler.spiders',
 'ROBOTSTXT_OBEY': True,
 'SPIDER_MODULES': ['newscrawler.spiders']}
2021-11-30 13:26:54 [scrapy.extensions.telnet] INFO: Telnet Password: 5c221c5a3423c146
2021-11-30 13:26:54 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.e

2021-11-30 13:26:55 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/sante/>
{'title': 'Comment le Covid-19 a « ruiné les progrès » récents en matière de dépistage et de prévention du sida', 'image': 'https://img.lemde.fr/2021/06/03/0/0/2868/1912/110/74/60/0/509e75f_923643679-000-hkg393499.jpg', 'description': 'A l’approche de la Journée mondiale de lutte contre le sida, mercredi\xa01er\xa0décembre, les associations s’alarment de la chute du nombre de tests de dépistage du VIH et craignent un rebond épidémique à court et moyen termes.'}
2021-11-30 13:26:55 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/campus/>
{'title': 'Manque de considération, maltraitance et burn-out : la grande fatigue des sages-femmes', 'image': 'https://img.lemde.fr/2021/11/22/90/0/7542/5028/110/74/60/0/eb8335b_25591854-sagefemmes-clr-01.jpeg', 'description': 'Epuisés par leurs études et leurs conditions de travail, étudiants et étudiantes sont de plus en plus nombreux

2021-11-30 13:26:55 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/sante/>
{'title': 'Covid-19 : la Haute Autorité de santé recommande de ne vacciner que les enfants à risque', 'image': 'https://img.lemde.fr/2021/11/30/1/0/7277/4851/110/74/60/0/d9a4cc1_286562386-667732.jpg', 'description': 'L’instance recommande d’«\xa0élargir dès à présent\xa0» l’administration du vaccin Pfizer aux enfants «\xa0à risque de forme grave\xa0», mais renvoie la généralisation en France à plus tard.'}
2021-11-30 13:26:55 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/sante/>
{'title': '« Les défenseurs de la “grande Sécu” n’ont pas dit leur dernier mot »', 'image': 'https://img.lemde.fr/2021/11/26/3/0/5900/3933/110/74/60/0/5b1221f_535926494-jmug211125006.jpg', 'description': 'Un collectif de soixante-neuf professionnels de santé, chercheurs et personnalités de l’éducation populaire et de la culture proteste, dans une tribune au «\xa0Monde\xa0», contre le risque 

2021-11-30 13:26:56 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/pixels/>
{'title': 'Un régulateur britannique ordonne à Facebook de vendre Giphy', 'image': 'https://img.lemde.fr/2021/11/18/0/144/3453/2302/110/74/60/0/1e470e2_846c296cb77d44f48a34177c63f2de8a-846c296cb77d44f48a34177c63f2de8a-0.jpg', 'description': 'Le mois dernier, le gendarme britannique de la concurrence avait infligé une amende de 50,5\xa0millions de livres au géant des réseaux sociaux dans le cadre de sa fusion avec Giphy, spécialisé dans les animations courtes sur Internet.'}
2021-11-30 13:26:56 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/disparitions/>
{'title': 'Mort de l’acteur aborigène David Dalaithngu, révélé mondialement dans « Crocodile Dundee »', 'image': 'https://img.lemde.fr/2021/11/30/945/0/3064/2040/110/74/60/0/8e41bc1_5106003-01-06.jpg', 'description': 'Lancé alors qu’il était adolescent grâce au film «\xa0La Randonnée\xa0», l’artiste australien a dér

2021-11-30 13:26:56 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/pixels/>
{'title': 'Immobilier : attention aux dossiers de location falsifiés', 'image': 'https://img.lemde.fr/2021/11/26/2629/0/5315/3532/110/74/60/0/ec1fe8e_76072625-pns-3045130.jpg', 'description': 'Gonfler ses revenus ou mentir sur sa situation professionnelle peut être tentant pour obtenir un logement. Comment le propriétaire peut-il vérifier les documents fournis\xa0? Comment le locataire peut-il lustrer son dossier sans tricher\xa0? Quelques conseils.'}
2021-11-30 13:26:56 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/pixels/>
{'title': 'Vente de matériel de cybersurveillance à l’Egypte : la société Nexa Technologies mise en examen', 'image': 'https://img.lemde.fr/2021/11/23/0/0/3840/2560/110/74/60/0/6bd48fe_222167937-000-8wm32h.jpg', 'description': 'L’enquête menée par le pôle crimes contre l’humanité du tribunal judiciaire de Paris a pour but de déterminer si un li

...

2021-11-30 13:26:58 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/immigration-en-europe/>
{'title': 'La colère des associations après la mort de 27 migrants dans la Manche : « C’étaient des hommes, des femmes, des enfants, des humains »', 'image': 'https://img.lemde.fr/2021/11/25/207/0/4252/2831/110/74/60/0/edb987f_886966410-l1030694-3.jpg', 'description': 'La plupart des victimes étaient des Kurdes, originaires d’Irak ou d’Iran. Après ce drame inédit, les autorités ciblent les passeurs et les ONG réclament des voies légales de migration vers le Royaume-Uni.'}
2021-11-30 13:26:58 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/immigration-en-europe/>
{'title': 'Après le naufrage de migrants dans la Manche, Boris Johnson appelle la France à une meilleure collaboration', 'image': 'https://img.lemde.fr/2021/11/25/0/0/3400/2266/110/74/60/0/5ac74ba_755620893-000-9ta73g.jpg', 'description': 'Les deux pays «\xa0sont convenus de l’urgence de renfor

2021-11-30 13:26:58 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/proces-des-attentats-du-13-novembre/>
{'title': 'Le dilemme des journalistes face aux propos de Salah Abdeslam', 'image': 'https://img.lemde.fr/2021/09/14/8/0/1500/1000/110/74/60/0/f025fc1_136053-3238466.jpg', 'description': 'Dès le début du procès des attentats du 13-Novembre, les médias ont été confrontés aux propos provocants du principal accusé, seul membre encore en vie du commando terroriste. Et s’interrogent sur la place à lui accorder.'}
2021-11-30 13:26:58 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/proces-des-attentats-du-13-novembre/>
{'title': 'Les policiers de la BAC75N, premiers à entrer dans le Bataclan et héros « oubliés » de l’assaut', 'image': 'https://img.lemde.fr/2021/09/17/641/802/3472/2314/110/74/60/0/58fd74f_751489399-v6a7294.jpg', 'description': 'Le soir du 13\xa0novembre\xa02015, l’intervention des membres de la BAC de nuit est restée longtemps ab

2021-11-30 13:26:58 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/coronavirus-2019-ncov/>
{'title': 'Assister à un concert masqué ne présente pas de risque de contamination aggravé', 'image': 'https://img.lemde.fr/2021/07/09/0/0/6000/4000/110/74/60/0/50321b9_964957763-choix-29052021-l2340627.jpg', 'description': 'L’étude menée à l’occasion d’un concert d’Indochine, en mai à Paris, montre que la jauge admise lors d’un spectacle influe peu sur le risque de transmission\xa0: seuls comptent vraiment les gestes barrières et le passe sanitaire.'}
2021-11-30 13:26:58 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/bielorussie/>
{'title': 'L’Europe veut sanctionner la Biélorussie, responsable d’un afflux de migrants à la frontière de la Pologne', 'image': 'https://img.lemde.fr/2021/11/08/0/0/3072/2048/110/74/60/0/eaf3cfe_5979956-01-06.jpg', 'description': 'L’Union européenne accuse le président biélorusse, Alexandre Loukachenko – lequel dément –, d

2021-11-30 13:26:58 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/immigration-en-europe/>
{'title': 'Pascal Brice, Daniel Cohn-Bendit et Romain Goupil : face à la crise migratoire, « l’UE ne peut pas se transformer en financeur de barbelés »', 'image': 'https://img.lemde.fr/2021/11/16/0/0/3072/2048/110/74/60/0/78fc3a6_5025544-01-06.jpg', 'description': 'L’ex-directeur de l’\xa0l’Office français de protection des réfugiés et apatrides, l’ancien député européen et le réalisateur prônent la fermeté à l’égard du régime biélorusse et exigent un accueil digne et maîtrisé des réfugiés, pour des raisons humanitaires et économiques.'}
2021-11-30 13:26:58 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/immigration-en-europe/>
{'title': 'A la frontière entre la Biélorussie et la Pologne, des milliers de migrants visés par des canons à eau et des gaz lacrymogènes', 'image': 'https://img.lemde.fr/2021/11/16/47/0/2831/1887/110/74/60/0/680e7d8_b178836968c

2021-11-30 13:26:58 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/coronavirus-2019-ncov/>
{'title': 'Guadeloupe : l’obligation vaccinale des soignants ne sera pas levée, selon le gouvernement', 'image': 'https://img.lemde.fr/2021/11/25/0/0/3885/2590/110/74/60/0/7dca9b6_5080452-01-06.jpg', 'description': 'Les maires de l’île avaient plaidé pour une suspension du dispositif lors d’une réunion en visioconférence avec le ministre des outre-mer, Sébastien Lecornu. Le ministère s’est engagé à appliquer la loi «\xa0avec proportionnalité et discernement\xa0».'}
2021-11-30 13:26:58 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/coronavirus-2019-ncov/>
{'title': 'Covid-19 : En Guyane, le couvre-feu est levé suite à la décrue de l’épidémie', 'image': 'https://img.lemde.fr/2021/11/25/85/0/2048/1365/110/74/60/0/5f85e52_30732113-kourou-beach.jpeg', 'description': 'Cinq communes dont Cayenne et Kourou y étaient toujours soumises de 22\xa0heures à 5\xa0he

In [25]:
!cd newscrawler && scrapy crawl lemondev3 -o lbc.xml

2021-11-30 13:27:01 [scrapy.utils.log] INFO: Scrapy 2.4.0 started (bot: newscrawler)
2021-11-30 13:27:01 [scrapy.utils.log] INFO: Versions: lxml 4.6.4.0, libxml2 2.9.10, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 20.3.0, Python 3.8.12 (default, Nov 17 2021, 16:58:51) - [GCC 10.2.1 20210110], pyOpenSSL 19.1.0 (OpenSSL 1.1.1h  22 Sep 2020), cryptography 3.2.1, Platform Linux-5.10.16.3-microsoft-standard-WSL2-x86_64-with-glibc2.2.5
2021-11-30 13:27:01 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.epollreactor.EPollReactor
2021-11-30 13:27:01 [scrapy.crawler] INFO: Overridden settings:
{'BOT_NAME': 'newscrawler',
 'NEWSPIDER_MODULE': 'newscrawler.spiders',
 'ROBOTSTXT_OBEY': True,
 'SPIDER_MODULES': ['newscrawler.spiders']}
2021-11-30 13:27:01 [scrapy.extensions.telnet] INFO: Telnet Password: 3bafdb57374ecddc
2021-11-30 13:27:01 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.e

2021-11-30 13:27:02 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/pixels/> (referer: https://www.lemonde.fr)
2021-11-30 13:27:02 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/sante/>
{'title': 'Comment le Covid-19 a « ruiné les progrès » récents en matière de dépistage et de prévention du sida', 'image': 'https://img.lemde.fr/2021/06/03/0/0/2868/1912/110/74/60/0/509e75f_923643679-000-hkg393499.jpg', 'description': 'A l’approche de la Journée mondiale de lutte contre le sida, mercredi\xa01er\xa0décembre, les associations s’alarment de la chute du nombre de tests de dépistage du VIH et craignent un rebond épidémique à court et moyen termes.'}
2021-11-30 13:27:02 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/afrique/>
{'title': 'Le Maroc disposé à favoriser une reprise des négociations entre Israël et Palestiniens', 'image': 'https://img.lemde.fr/2021/11/30/0/0/2250/1500/110/74/60/0/fecb7fe_278284556-000-9tb4y4.jpg', 

2021-11-30 13:27:02 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/sport/> (referer: https://www.lemonde.fr)
2021-11-30 13:27:02 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/sante/>
{'title': 'Omicron : le nouveau variant détecté dans de plus en plus de pays, l’OMS s’inquiète d’un « risque très élevé » à l’échelle planétaire', 'image': 'https://img.lemde.fr/2021/11/29/0/0/3500/2333/110/74/60/0/9c508bb_ggg-aus101-health-coronavirus-australia-1129-11.jpg', 'description': 'L’Organisation mondiale de la santé estime que le variant du SARS-CoV-2 présente un nombre de mutations «\xa0sans précédent\xa0», dont plusieurs «\xa0sont préoccupantes en raison de leur impact potentiel sur la trajectoire de l’épidémie\xa0» de Covid-19.'}
2021-11-30 13:27:02 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/sante/>
{'title': '« Grande Sécu » : « Les primes des complémentaires sont doublement inégalitaires, aux dépens des plus pauvres e

2021-11-30 13:27:02 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/afrique/>
{'title': 'RDC : l’attaque d’un camp de déplacés fait vingt-deux morts en Ituri', 'image': 'https://img.lemde.fr/2021/11/22/0/0/3600/2400/110/74/60/0/6adf46d_5064392-01-06.jpg', 'description': 'Les miliciens du groupe Codeco, qui prétend défendre les intérêts de la communauté des Lendu de cette province, sont soupçonnés d’être responsables de l’assaut.'}
2021-11-30 13:27:02 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/afrique/>
{'title': 'En RDC, l’armée ougandaise autorisée à passer la frontière pour traquer les rebelles ADF', 'image': 'https://img.lemde.fr/2021/11/16/0/0/4093/2728/110/74/60/0/5edc48f_9c90fa69f8304308a1a6479c68cdd49b-9c90fa69f8304308a1a6479c68cdd49b-0.jpg', 'description': 'Certains voient cette décision comme une «\xa0solution provisoire\xa0» avant une réorganisation de l’armée congolaise, alors que près de 1\xa0200 civils ont été massacrés dans

2021-11-30 13:27:02 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/pixels/>
{'title': 'Un régulateur britannique ordonne à Facebook de vendre Giphy', 'image': 'https://img.lemde.fr/2021/11/18/0/144/3453/2302/110/74/60/0/1e470e2_846c296cb77d44f48a34177c63f2de8a-846c296cb77d44f48a34177c63f2de8a-0.jpg', 'description': 'Le mois dernier, le gendarme britannique de la concurrence avait infligé une amende de 50,5\xa0millions de livres au géant des réseaux sociaux dans le cadre de sa fusion avec Giphy, spécialisé dans les animations courtes sur Internet.'}
2021-11-30 13:27:02 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/campus/>
{'title': 'La FAGE, école du terrain pour les futurs responsables politiques', 'image': 'https://img.lemde.fr/2021/04/27/0/0/5568/3712/110/74/60/0/e64d4ed_981380121-000-13f924.jpg', 'description': 'Le syndicat étudiant, qui se dit apartisan, a «\xa0formé\xa0» de nombreux jeunes qui ont ensuite intégré des cabinets ou se s

...

2021-11-30 13:27:04 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/vaccins-contre-le-covid-19/>
{'title': 'Qui sont les 17 000 enfants de moins de 12 ans déjà vaccinés contre le Covid-19 en France ?', 'image': 'https://img.lemde.fr/2021/11/23/0/0/5472/3648/110/74/60/0/569c2e1_817548299-000-9t72jf.jpg', 'description': 'Contrairement aux Etats-Unis ou à Israël, la France n’a pas ouvert la vaccination aux jeunes enfants. Pourtant, les exceptions se multiplient, avec des justifications diverses.'}
2021-11-30 13:27:04 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/vaccins-contre-le-covid-19/>
{'title': 'Vaccin contre le Covid-19 : la perspective d’une troisième dose pour tous les adultes se précise', 'image': 'https://img.lemde.fr/2021/11/17/0/17/3465/2310/110/74/60/0/027fda6_gggmahe03-health-coronavirus-france-1117-11.jpg', 'description': 'Selon le conseil scientifique et le conseil d’orientation de la stratégie vaccinale, l’élargissement du ra

2021-11-30 13:27:04 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/climat/>
{'title': 'Le Var, désormais unique département en vigilance orange', 'image': 'https://img.lemde.fr/2021/10/30/109/0/1010/672/110/74/60/0/d1cf4f5_373756965-capture-d-e-cran-2021-10-30-a-22-54-53.png', 'description': 'La situation pluvio-orageuse localisée dans le Var nécessite une vigilance particulière au vu de son intensité. L’Ardèche, le Gard et la Lozère sortent de la vigilance.'}
2021-11-30 13:27:04 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/international/>
{'title': 'A Vienne, retrouvailles diplomatiques tendues autour du nucléaire iranien', 'image': 'https://img.lemde.fr/2021/11/26/8/0/3894/2596/110/74/60/0/4b97b95_877092670-649508.jpg', 'description': 'Alors que les négociations reprennent lundi 29 novembre dans la capitale autrichienne, les motifs d’inquiétude s’accumulent et l’espoir de sauver l’accord de 2015 est mince.'}
2021-11-30 13:27:04 [scrapy.

2021-11-30 13:27:05 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/coronavirus-2019-ncov/>
{'title': 'Le nouveau variant Omicron assombrit l’horizon économique', 'image': 'https://img.lemde.fr/2021/11/27/16/0/4336/2885/110/74/60/0/2cd4e28_642698437-249350.jpg', 'description': 'Partout en Europe, les restrictions budgétaires se multiplient. La croissance devrait être presque nulle au quatrième trimestre en zone euro et les marchés boursiers s’inscrivent en forte baisse.'}
2021-11-30 13:27:05 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/coronavirus-2019-ncov/>
{'title': 'A l’aéroport de Casablanca, le désarroi des voyageurs à destination de la France', 'image': 'https://img.lemde.fr/2021/11/26/0/0/4645/3096/110/74/60/0/e890b62_326255139-ap-20197670050779.jpg', 'description': 'Les voyageurs ont dû s’organiser dans l’urgence, après l’annonce soudaine des autorités marocaines de la suspension des vols, due à la situation sanitaire en France.'}

2021-11-30 13:27:05 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/election-presidentielle-2022/>
{'title': 'Akira, ce collectif anonyme aux idées révolutionnaires qui veut se faire entendre pendant la campagne présidentielle', 'image': 'https://img.lemde.fr/2021/11/19/364/291/1901/1267/110/74/60/0/04967d8_745972720-capture-d-e-cran-2021-11-19-a-11-13-40.jpeg', 'description': 'Une femme masquée a annoncé la candidature collective et symbolique d’un groupe qui ne se reconnaît dans aucun «\xa0mot en «\xa0isme\xa0»\xa0», ni dans aucun camp.'}
2021-11-30 13:27:05 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/election-presidentielle-2022/>
{'title': 'Eric Zemmour, nouveau pôle d’attraction de l’ultradroite', 'image': 'https://img.lemde.fr/2021/11/19/0/0/5472/3648/110/74/60/0/5bad56f_561473929-000-9q49l6.jpg', 'description': 'De nombreux militants de l’extrême droite la plus radicale et violente, qui jugent Marine Le Pen trop modérée, soutiennen

2021-11-30 13:27:05 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/coronavirus-2019-ncov/>
{'title': 'Emmanuel Macron veut faire peser la contrainte sur les non-vaccinés', 'image': 'https://img.lemde.fr/2021/11/26/71/0/7359/4906/110/74/60/0/e2a87e6_726021797-656736.jpg', 'description': 'A cinq mois de la présidentielle, le chef de l’Etat ne veut pas recourir à des restrictions sociales fortes pour faire face au redémarrage de l’épidémie, mais cherche à pousser toujours plus la vaccination.'}
2021-11-30 13:27:05 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/coronavirus-2019-ncov/>
{'title': 'Guadeloupe : l’obligation vaccinale des soignants ne sera pas levée, selon le gouvernement', 'image': 'https://img.lemde.fr/2021/11/25/0/0/3885/2590/110/74/60/0/7dca9b6_5080452-01-06.jpg', 'description': 'Les maires de l’île avaient plaidé pour une suspension du dispositif lors d’une réunion en visioconférence avec le ministre des outre-mer, Sébastien L


## Votre premier Item

La classe `Item` permet de structurer les données que l'on souhaite
récupérer sous la forme d'un modèle. Les items doivent être définis dans
le fichier `items.py` créé par la commande `scrapy startproject`. Les
`Item` héritent de la class `scrapy.Item`.

On veut structurer les données avec deux champs : le titre et le prix de
l'annonce. Scrapy utilise une classe `scrapy.Field` permettant de
'déclarer' ces champs. Dans notre cas :

In [28]:
# %load newscrawler/newscrawler/items.py

# Define here the models for your scraped items
#
# See documentation in:
# https://docs.scrapy.org/en/latest/topics/items.html

import scrapy

class ArticleItem(scrapy.Item):
    title = scrapy.Field()
    image = scrapy.Field()
    description = scrapy.Field()

Utiliser la classe `scrapy.Item` plutôt qu'un simple dictionnaire permet
plus de contrôle sur la structure des données. En effet, on ne peut
insérer dans les items que des données avec des clés 'déclarées'. Ce qui
assure une plus grande cohérence au sein d'un projet.

On peut instancier un item de plusieurs façons :

In [29]:
article_item = ArticleItem(title="Gilets Jaunes", image=None, description="Un samedi de manifestations")

In [30]:
print(article_item)

{'description': 'Un samedi de manifestations',
 'image': None,
 'title': 'Gilets Jaunes'}


In [31]:
article_item = ArticleItem()
article_item["title"] = 'Gilets Jaunes'
article_item["description"] = 'Un samedi de manifestations'

In [32]:
print(article_item)

{'description': 'Un samedi de manifestations', 'title': 'Gilets Jaunes'}


La définition d'un item permet de palier toutes les erreurs de typo dans
les champs.

In [33]:
article_item = ArticleItem()
article_item["titelkjwnxvmnscbvmknxc"] = 'Gilets Jaunes'

KeyError: 'ArticleItem does not support field: titelkjwnxvmnscbvmknxc'

Les items héritent des dictionnaires Python, et possèdent donc toutes
les méthodes de ceux-ci:

In [37]:
article_item = ArticleItem(title="Gilets Jaunes")
print(article_item["title"]) # Méthode __getitem__()
print(article_item.get("description", "no description provided")) # Méthode get()
print(article_item.get("description")) # Méthode get()

Gilets Jaunes
no description provided
None


On peut transformer un `Item` en dictionnaire très facilement, en le
passant au constructeur:

In [31]:
article_item = ArticleItem(title="Drone DJI")
print(type(article_item))
dict_item = dict(article_item)
print(type(dict_item))
print(dict_item)

<class '__main__.ArticleItem'>
<class 'dict'>
{'title': 'Drone DJI'}


On intègre maintenant cet item dans notre spider.

In [ ]:
# -*- coding: utf-8 -*-
import scrapy
from scrapy import Request
from ..items import ArticleItem
class LemondeSpider(scrapy.Spider):
    name = "lemonde"
    allowed_domains = ["www.lemonde.fr"]
    start_urls = ['https://www.lemonde.fr']

    def parse(self, response):
        title = response.css('title::text').extract_first()
        all_links = {
            name:response.urljoin(url) for name, url in zip(
            response.css("#nav-markup .Nav__item")[3].css("a::text").extract(),
            response.css("#nav-markup .Nav__item")[3].css("a::attr(href)").extract())
        }
        for link in all_links.values():
            yield Request(link, callback=self.parse_category)

    def parse_category(self, response):
        for article in response.css(".fleuve")[0].css("article"):
            title = self.clean_spaces(article.css("h3 a::text").extract_first())
            image = article.css("img::attr(data-src)").extract_first()
            description = article.css(".txt3::text").extract_first()

            yield ArticleItem(
                title=title,
                image=image,
                description=description
            )

    def clean_spaces(self, string):
        if string:
            return " ".join(string.split())

On voit bien que le générateur retourne maintenant un `Item`.

### Exercice : 

Relancer la spider pour vérifier le bon déroulement de l'extraction.


In [38]:
!cd newscrawler/ && scrapy crawl lemondev4

2021-11-30 13:40:57 [scrapy.utils.log] INFO: Scrapy 2.4.0 started (bot: newscrawler)
2021-11-30 13:40:58 [scrapy.utils.log] INFO: Versions: lxml 4.6.4.0, libxml2 2.9.10, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 20.3.0, Python 3.8.12 (default, Nov 17 2021, 16:58:51) - [GCC 10.2.1 20210110], pyOpenSSL 19.1.0 (OpenSSL 1.1.1h  22 Sep 2020), cryptography 3.2.1, Platform Linux-5.10.16.3-microsoft-standard-WSL2-x86_64-with-glibc2.2.5
2021-11-30 13:40:58 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.epollreactor.EPollReactor
2021-11-30 13:40:58 [scrapy.crawler] INFO: Overridden settings:
{'BOT_NAME': 'newscrawler',
 'NEWSPIDER_MODULE': 'newscrawler.spiders',
 'ROBOTSTXT_OBEY': True,
 'SPIDER_MODULES': ['newscrawler.spiders']}
2021-11-30 13:40:58 [scrapy.extensions.telnet] INFO: Telnet Password: 4677767c37d76650
2021-11-30 13:40:58 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.e

2021-11-30 13:40:59 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/afrique/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/11/30/0/0/2250/1500/110/74/60/0/fecb7fe_278284556-000-9tb4y4.jpg',
 'title': 'Le Maroc disposé à favoriser une reprise des négociations entre '
          'Israël et Palestiniens'}
2021-11-30 13:40:59 [scrapy.core.scraper] ERROR: Spider error processing <GET https://www.lemonde.fr/le-monde-et-vous/> (referer: https://www.lemonde.fr)
Traceback (most recent call last):
  File "/root/.local/share/virtualenvs/code-AFz48Hjb/lib/python3.8/site-packages/scrapy/utils/defer.py", line 120, in iter_errback
    yield next(it)
  File "/root/.local/share/virtualenvs/code-AFz48Hjb/lib/python3.8/site-packages/scrapy/utils/python.py", line 353, in __next__
    return next(self.data)
  File "/root/.local/share/virtualenvs/code-AFz48Hjb/lib/python3.8/site-packages/scrapy/utils/python.py", line 353, in __next__
    return next(self.data)
  File "/roo

2021-11-30 13:40:59 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/afrique/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/11/29/1/0/5000/3333/110/74/60/0/ea024cb_625226901-000-9tl8mh.jpg',
 'title': 'Trente rhinocéros blancs introduits, en Boeing 747, au Rwanda'}
2021-11-30 13:40:59 [scrapy.core.scraper] ERROR: Spider error processing <GET https://www.lemonde.fr/podcasts/> (referer: https://www.lemonde.fr)
Traceback (most recent call last):
  File "/root/.local/share/virtualenvs/code-AFz48Hjb/lib/python3.8/site-packages/scrapy/utils/defer.py", line 120, in iter_errback
    yield next(it)
  File "/root/.local/share/virtualenvs/code-AFz48Hjb/lib/python3.8/site-packages/scrapy/utils/python.py", line 353, in __next__
    return next(self.data)
  File "/root/.local/share/virtualenvs/code-AFz48Hjb/lib/python3.8/site-packages/scrapy/utils/python.py", line 353, in __next__
    return next(self.data)
  File "/root/.local/share/virtualenvs/code-AFz48Hjb/lib/p

2021-11-30 13:40:59 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/afrique/>
{'description': None,
 'image': 'https://img.lemde.fr/2017/11/28/0/0.5/3499/2332/110/74/60/0/c55e529_PHW06_AFRICA-FRANCE-MACRON_1128_11.JPG',
 'title': 'Thomas Borrel et Antoine Glaser : « Un retrait militaire français '
          'd’Afrique serait un marqueur de rupture »'}
2021-11-30 13:40:59 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/afrique/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/11/26/0/0/2784/1856/110/74/60/0/6781584_696672112-dsc3521.jpg',
 'title': 'Le pari risqué des Chinois installés au Soudan du Sud'}
2021-11-30 13:40:59 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/afrique/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/11/26/0/164/3172/2115/110/74/60/0/9a37437_301035848-850615.jpg',
 'title': '« Chinafrique », l’heure des désillusions'}
2021-11-30 13:40:59 [scrapy.core.scraper] DEBUG: Scrape

2021-11-30 13:41:00 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/afrique/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/11/27/0/2/2332/1555/110/74/60/0/835c4b2_739060372-algerie.jpeg',
 'title': 'Algérie : les électeurs appelés aux urnes pour des scrutins locaux'}
2021-11-30 13:41:00 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/afrique/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/11/26/0/49/3166/2111/110/74/60/0/493dd64_240919156-livre-elgas.jpg',
 'title': 'Avec « Mâle noir », Elgas renouvelle avec brio le genre du roman de '
          'formation'}
2021-11-30 13:41:00 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/afrique/>
{'description': None,
 'image': 'https://img.lemde.fr/2014/10/30/0/0/3870/2576/110/74/60/0/742fcf4_32462-aj7zuf.jpg',
 'title': 'Dalila Kerchouche : « Enfant des camps de harkis, je ne donne pas '
          'le droit à l’Etat de chiffrer ma souffrance »'}
2021-11-

...

2021-11-30 13:41:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/international/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/11/22/60/0/1500/999/110/74/60/0/3f614d2_154471-3248618.jpg',
 'title': '« On sait que vous protégez les coupables, on ne vous lâchera pas » '
          ': à Beyrouth, des agitatrices en quête de vérité'}
2021-11-30 13:41:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/international/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/11/27/0/0/5184/3456/110/74/60/0/84c86c8_efa0ba1a46cd463b9adf21197f288a7a-efa0ba1a46cd463b9adf21197f288a7a-0.jpg',
 'title': 'Migrants dans la Manche : pour l’Europe, c’est à Londres de gérer '
          'le contrôle de ses frontières'}
2021-11-30 13:41:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/international/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/05/08/0/25/3450/2300/110/74/60/0/6962eb0_gggyh07-europe-day-schum

2021-11-30 13:41:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/election-presidentielle-2022/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/11/18/1/0/8192/5461/110/74/60/0/655b2bf_671195665-000-9re77c.jpg',
 'title': 'Jean Pisani-Ferry : « Dans l’optique de la présidentielle 2022, la '
          'clarté sur les choix est une condition de la légitimité de l’action '
          'à venir »'}
2021-11-30 13:41:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/election-presidentielle-2022/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/11/20/0/0/5108/3405/110/74/60/0/9be416e_985283943-590670.jpg',
 'title': 'Entre 2017 et 2022, La France insoumise a amendé son programme à la '
          'marge'}
2021-11-30 13:41:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/election-presidentielle-2022/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/11/18/0/0/3900/2600/110/74/60/0/e3916ed_503992

2021-11-30 13:41:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/vaccins-contre-le-covid-19/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/07/16/0/17/3465/2310/110/74/60/0/a388b67_fw1-health-coronavirus-france-vaccination-0716-11.jpg',
 'title': 'Les Français plus circonspects qu’antivaccin'}
2021-11-30 13:41:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/vaccins-contre-le-covid-19/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/11/17/0/6/5934/3956/110/74/60/0/82bec81_5033846-01-06.jpg',
 'title': 'Quatrième jour de mobilisation en Guadeloupe contre le passe '
          'sanitaire et l’obligation vaccinale'}
2021-11-30 13:41:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/vaccins-contre-le-covid-19/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/11/17/0/0/3000/2000/110/74/60/0/c8d6fef_81422325-025-msf-briancon-julien-benard.jpg',
 'title': '« Les enjeux sanitaires ne doiv

2021-11-30 13:41:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/bielorussie/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/09/07/88/0/1848/1230/110/74/60/0/30dd2fa_492199675-667922.jpg',
 'title': 'En Biélorussie, la figure de l’opposition Maria Kolesnikova '
          'condamnée à onze ans de prison'}
2021-11-30 13:41:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/bielorussie/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/09/06/0/67/2866/1911/110/74/60/0/4d30ab1_5585124-01-06.jpg',
 'title': 'L’opposante Maria Kolesnikova condamnée à onze ans de prison en '
          'Biélorussie'}
2021-11-30 13:41:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/proces-des-attentats-du-13-novembre/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/09/09/137/124/4580/3053/110/74/60/0/da044b2_949790955-brun-proces01006.jpg',
 'title': 'Au deuxième jour du procès du 13-Novembre, Salah Abdesl

2021-11-30 13:41:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/coronavirus-2019-ncov/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/11/25/0/17/5782/3858/110/74/60/0/7c9240b_744190146-000-93r29q.jpg',
 'title': '« On n’avait jamais connu ça » : le nombre de classes fermées pour '
          'cause de Covid-19 a doublé en une semaine'}
2021-11-30 13:41:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/coronavirus-2019-ncov/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/11/26/0/13/4974/3316/110/74/60/0/f29cb66_615078797-2021-11-25t112539z-665301519-rc2n1r9ishxv-rtrmadp-3-health-coronavirus-africa.JPG',
 'title': 'Covid-19 en Afrique : seul un professionnel de santé sur quatre est '
          'entièrement vacciné'}
2021-11-30 13:41:01 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.lemonde.fr/coronavirus-2019-ncov/>
{'description': None,
 'image': 'https://img.lemde.fr/2021/11/26/0/0/3499/2333/110/74/60

## Postprocessing

Si l'on se réfère au diagramme d'architecture de Scrapy, on voit qu'il
est possible d'insérer des composants supplémentaires dans le flux de
traitement. Ces composants s'appellent `Pipelines`.

Par défaut, tous les `Item` générés au sein d'un projet Scrapy passent
par les `Pipelines`. Les pipelines sont utilisés la plupart du temps
pour :

-   Nettoyer du contenu HTML ;
-   Valider les données scrapées ;
-   Supprimer les items qu'on ne souhaite pas stocker ;
-   Stocker ces objets dans des bases de données.

Les pipelines doivent être définis dans le fichier `pipelines.py`.

Dans notre cas on peut vouloir nettoyer le champ `title` pour enlever
les caractères superflus.

Nous allons alors transferer la fonction de nettoyage du code html dans
une Pipeline.

In [ ]:
# %load newscrawler/newscrawler/pipelines.py

# Define your item pipelines here
#
# Don't forget to add your pipeline to the ITEM_PIPELINES setting
# See: https://docs.scrapy.org/en/latest/topics/item-pipeline.html

from scrapy.exceptions import DropItem

class TextPipeline(object):

    def process_item(self, item, spider):
        if item['title']:
            item["title"] = clean_spaces(item["title"])
            return item
        else:
            raise DropItem("Missing title in %s" % item)


def clean_spaces(string):
    if string:
        return " ".join(string.split())

Pour dire au process Scrapy de faire transiter les items par ces
pipelines. Il faut le spécifier dans le fichier de paramétrage
`settings.py`.

In [ ]:
ITEM_PIPELINES = {
     'newscrawler.pipelines.TextPipeline': 300,
 }

On peut maintenant supprimer la fonction `clean_spaces()` de
l'extraction des données et laisser le Pipeline faire son travail. La
valeur entière définie permet de déterminer l'ordre dans lequel les
pipelines vont être appelés. Ces entiers peuvent être compris entre 0 et
1000.

On relance notre spider :

In [ ]:
!cd newscrawler/ && scrapy crawl lemondev5 -o ../data/articles.json

2021-11-30 14:03:32 [scrapy.utils.log] INFO: Scrapy 2.4.0 started (bot: newscrawler)
2021-11-30 14:03:32 [scrapy.utils.log] INFO: Versions: lxml 4.6.4.0, libxml2 2.9.10, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 20.3.0, Python 3.8.12 (default, Nov 17 2021, 16:58:51) - [GCC 10.2.1 20210110], pyOpenSSL 19.1.0 (OpenSSL 1.1.1h  22 Sep 2020), cryptography 3.2.1, Platform Linux-5.10.16.3-microsoft-standard-WSL2-x86_64-with-glibc2.2.5
2021-11-30 14:03:32 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.epollreactor.EPollReactor
2021-11-30 14:03:32 [scrapy.crawler] INFO: Overridden settings:
{'BOT_NAME': 'newscrawler',
 'NEWSPIDER_MODULE': 'newscrawler.spiders',
 'ROBOTSTXT_OBEY': True,
 'SPIDER_MODULES': ['newscrawler.spiders']}
2021-11-30 14:03:32 [scrapy.extensions.telnet] INFO: Telnet Password: 4ce7df12ccfab9e4
2021-11-30 14:03:32 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.e

2021-11-30 14:03:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/campus/> (referer: https://www.lemonde.fr)
2021-11-30 14:03:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/sante/> (referer: https://www.lemonde.fr)
2021-11-30 14:03:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/afrique/> (referer: https://www.lemonde.fr)
2021-11-30 14:03:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/le-monde-et-vous/> (referer: https://www.lemonde.fr)
2021-11-30 14:03:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/big-browser/> (referer: https://www.lemonde.fr)
2021-11-30 14:03:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/pixels/> (referer: https://www.lemonde.fr)
2021-11-30 14:03:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.lemonde.fr/disparitions/> (referer: https://www.lemonde.fr)
2021-11-30 14:03:34 [scrapy.core.engine] DEBUG: 

On peut aussi utiliser les Pipelines pour stocker les données récupérées
dans une base de données. Pour stocker les items dans des documents
mongo :

In [ ]:
import pymongo

class MongoPipeline(object):

    collection_name = 'scrapy_items'

    def open_spider(self, spider):
        self.client = pymongo.MongoClient()
        self.db = self.client["lemonde"]

    def close_spider(self, spider):
        self.client.close()

    def process_item(self, item, spider):
        self.db[self.collection_name].insert_one(dict(item))
        return item

Ici on redéfinit deux autres méthodes: `open_spider()`et
`close_spider()`, ces méthodes sont appelées comme leur nom l'indique,
lorsque la Spider est instanciée et fermée.

Ces méthodes nous permettent d'ouvrir la connexion Mongo et de la fermer
lorsque le scraping se termine. La méthode `process_item()` est appelé à
chaque fois qu'un item passe dans le mécanisme interne de scrapy. Ici,
la méthode permet d'insérer l'item en tant que document mongo.

Pour que ce pipeline soit appelé il faut l'ajouter dans les settings du
projet.

In [ ]:
ITEM_PIPELINES = {
    'newscrawler.pipelines.TextPipeline': 100,
    'newscrawler.pipelines.MongoPipeline': 300
}

Le pipeline est ajoutée à la fin du process pour profiter des deux
précédents.

## Settings

Scrapy permet de gérer le comportement des spiders avec certains
paramètres. Comme expliqué dans le premier cours, il est important de
suivre des règles en respectant la structure des différents sites. Il
existe énormément de paramètres mais nous allons (dans le cadre de ce
cours) aborder les plus utilisés :

-   DOWNLOAD\_DELAY : Le temps de téléchargement entre chaque requête
    sur le même domaine ;
-   CONCURRENT\_REQUESTS\_PER\_DOMAIN : Nombre de requêtes simultanées
    par domaine ;
-   CONCURRENT\_REQUESTS\_PER\_IP : Nombre de requêtes simultanées par
    IP ;
-   DEFAULT\_REQUEST\_HEADERS : Headers HTTP utilisés pour les requêtes
    ;
-   ROBOTSTXT\_OBEY : Scrapy récupère le robots.txt et adapte le
    scraping en fonction des règles trouvées ;
-   USER\_AGENT : UserAgent utilisé pour faire les requêtes ;
-   BOT\_NAME : Nom du bot annoncé lors des requêtes
-   HTTPCACHE\_ENABLED : Utilisation du cache HTTP, utile lors du
    parcours multiple de la même page.

Le fichiers `settings.py` permet de définir les paramètres globaux d'un
projet. Si votre projet contient un grand nombre de spiders, il peut
être intéressant d'avoir des paramètres distincts pour chaque spider. Un
moyen simple est d'ajouter un attribut `custom_settings` à votre spider
:

In [ ]:
class LeMondeSpider(scrapy.Spider):
        name = "lemonde"
        allowed_domains = ["lemonde.fr"]
        start_urls = ['http://lemonde.fr/']
        custom_settings = {
            "HTTPCACHE_ENABLED":True, 
            "CONCURRENT_REQUESTS_PER_DOMAIN":100
        }